<a href="https://colab.research.google.com/github/alvin-98/English-Premier-League-2021-22-Prediction/blob/main/English_Premier_League_2021_22_Prediction.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
# Here we import the packages we will need
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import statsmodels.api as sm
import statsmodels.formula.api as smf
import plotly.express as px

In [ ]:
wagedat=pd.read_excel("Latest 10-12-2021 - EPL club wages and position 1997-2021.xlsx")
TMdat = pd.read_excel("Latest 22 - EPL TM values 2010-11 to 2021-22.xlsx")

In [ ]:
# Because of the promotion and relegation system, there are many more than 20 clubs in our data, even though there were only ever 20 clubs in the Premier League in any one season. 
#We can see which clubs appeared by listing the unique elements of the "Club" variable in our wage data file.

wagedat['Club'].unique()

array(['Arsenal', 'Aston Villa', 'Barnsley', 'Birmingham City',
       'Blackburn Rovers', 'Blackpool', 'Bolton Wanderers', 'Bournemouth',
       'Bradford City', 'Brighton & Hove Albion', 'Burnley',
       'Cardiff City', 'Charlton Athletic', 'Chelsea', 'Coventry City',
       'Crystal Palace', 'Derby County', 'Everton', 'Fulham',
       'Huddersfield Town', 'Hull City', 'Ipswich Town', 'Leeds United',
       'Leicester City', 'Liverpool', 'Manchester City',
       'Manchester United', 'Middlesbrough', 'Newcastle United',
       'Norwich City', 'Nottingham Forest', 'Portsmouth',
       'Queens Park Rangers', 'Reading', 'Sheffield United',
       'Sheffield Wednesday', 'Southampton', 'Stoke City', 'Sunderland',
       'Swansea City', 'Tottenham Hotspur', 'Watford',
       'West Bromwich Albion', 'West Ham United', 'Wigan Athletic',
       'Wimbledon', 'Wolverhampton Wanderers'], dtype=object)

In [ ]:
# Likewise we can list the unique elements of the "Club" variable in the TM data. Note this has fewer clubs, since the data covers a shorter period.

TMdat['Club'].unique()

array(['Arsenal', 'Aston Villa', 'Birmingham City', 'Blackburn Rovers',
       'Blackpool', 'Bolton Wanderers', 'Chelsea', 'Everton', 'Fulham',
       'Liverpool', 'Manchester City', 'Manchester United',
       'Newcastle United', 'Stoke City', 'Sunderland',
       'Tottenham Hotspur', 'West Bromwich Albion', 'West Ham United',
       'Wigan Athletic', 'Wolverhampton Wanderers', 'Norwich City',
       'Queens Park Rangers', 'Swansea City', 'Reading', 'Southampton',
       'Cardiff City', 'Crystal Palace', 'Hull City', 'Burnley',
       'Leicester City', 'Bournemouth', 'Watford', 'Middlesbrough',
       'Brighton & Hove Albion', 'Huddersfield Town', 'Sheffield United',
       'Leeds United', 'Brentford'], dtype=object)

In [ ]:
# We can use .shape to view the the dimensions of the wage data...

print(wagedat.shape)
print(TMdat.shape)

(500, 4)
(240, 4)


In [ ]:
wagedat.head()

seasonyrend     Club  Position       wages
0         1997  Arsenal       3.0  15279000.0
1         1998  Arsenal       1.0  21882000.0
2         1999  Arsenal       2.0  26478000.0
3         2000  Arsenal       2.0  33970000.0
4         2001  Arsenal       2.0  40651000.0

In [ ]:
TMdat.head()

seasonyrbegin  seasonyrend              Club  TMValue
0           2010         2011           Arsenal   272.70
1           2010         2011       Aston Villa   127.94
2           2010         2011   Birmingham City    68.00
3           2010         2011  Blackburn Rovers    65.93
4           2010         2011         Blackpool    24.37

In [ ]:
wagedat['teamid'] = wagedat['Club']+wagedat['seasonyrend'].map(str)
wagedat

seasonyrend  ...                       teamid
0           1997  ...                  Arsenal1997
1           1998  ...                  Arsenal1998
2           1999  ...                  Arsenal1999
3           2000  ...                  Arsenal2000
4           2001  ...                  Arsenal2001
..           ...  ...                          ...
495         2011  ...  Wolverhampton Wanderers2011
496         2012  ...  Wolverhampton Wanderers2012
497         2019  ...  Wolverhampton Wanderers2019
498         2020  ...  Wolverhampton Wanderers2020
499         2021  ...  Wolverhampton Wanderers2021

[500 rows x 5 columns]

In [ ]:
# create the same team/year id in TMdat

TMdat['teamid'] = TMdat['Club']+TMdat['seasonyrend'].map(str)
TMdat

seasonyrbegin  seasonyrend  ... TMValue                teamid
0             2010         2011  ...  272.70           Arsenal2011
1             2010         2011  ...  127.94       Aston Villa2011
2             2010         2011  ...   68.00   Birmingham City2011
3             2010         2011  ...   65.93  Blackburn Rovers2011
4             2010         2011  ...   24.37         Blackpool2011
..             ...          ...  ...     ...                   ...
235           2021         2022  ...  220.86  Newcastle United2022
236           2021         2022  ...  179.96         Brentford2022
237           2021         2022  ...  167.81      Norwich City2022
238           2021         2022  ...  130.95           Watford2022
239           2021         2022  ...  130.77           Burnley2022

[240 rows x 5 columns]

In [ ]:
TMdat = pd.merge(TMdat,wagedat[['Position','teamid','wages']], on= 'teamid', how = 'left')
TMdat

seasonyrbegin  seasonyrend  ... Position        wages
0             2010         2011  ...      4.0  124401000.0
1             2010         2011  ...      9.0   83395000.0
2             2010         2011  ...     18.0   45088340.0
3             2010         2011  ...     15.0   49869577.0
4             2010         2011  ...     19.0   26014248.0
..             ...          ...  ...      ...          ...
235           2021         2022  ...      NaN          NaN
236           2021         2022  ...      NaN          NaN
237           2021         2022  ...      NaN          NaN
238           2021         2022  ...      NaN          NaN
239           2021         2022  ...      NaN          NaN

[240 rows x 7 columns]

In [ ]:
# The TM data is expressed in £ million, while the wage data is in £. We can convert to common units by dividing wages by 1 million, 
# although this is not strictly necessary for the purpose of measuring correlation.

TMdat['wages']=TMdat['wages']/1000000
TMdat

seasonyrbegin  seasonyrend  ... Position       wages
0             2010         2011  ...      4.0  124.401000
1             2010         2011  ...      9.0   83.395000
2             2010         2011  ...     18.0   45.088340
3             2010         2011  ...     15.0   49.869577
4             2010         2011  ...     19.0   26.014248
..             ...          ...  ...      ...         ...
235           2021         2022  ...      NaN         NaN
236           2021         2022  ...      NaN         NaN
237           2021         2022  ...      NaN         NaN
238           2021         2022  ...      NaN         NaN
239           2021         2022  ...      NaN         NaN

[240 rows x 7 columns]

In [ ]:
TMdatNoZero = TMdat.dropna(inplace=False)
TMdatNoZero.shape

(201, 7)

In [ ]:
fig = px.scatter(x=TMdatNoZero.wages, y=TMdatNoZero.TMValue, color=TMdatNoZero.seasonyrend, trendline='ols')
fig.show()

In [ ]:
fig = px.scatter(x=TMdatNoZero.Position, y=TMdatNoZero.wages, color=TMdatNoZero.seasonyrend, trendline='ols')
fig.show()

In [ ]:
fig = px.scatter(x=TMdatNoZero.Position, y=TMdatNoZero.TMValue, color=TMdatNoZero.seasonyrend, trendline='ols')
fig.show()

In [ ]:
TMwage_lm = smf.ols(formula = 'TMValue ~ wages', data=TMdatNoZero).fit()
TMwage_lm.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                TMValue   R-squared:                       0.848
Model:                            OLS   Adj. R-squared:                  0.847
Method:                 Least Squares   F-statistic:                     1108.
Date:                Tue, 14 Dec 2021   Prob (F-statistic):           2.85e-83
Time:                        08:42:23   Log-Likelihood:                -1161.1
No. Observations:                 201   AIC:                             2326.
Df Residuals:                     199   BIC:                             2333.
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept    -75.9393     10.505     -7.229      0.000     -96.654     -55.224
wages          2.6173      0.079     33.286      0.000       2.462       2.772
==============================================================================
Omnibus:                      124.786   Durbin-Watson:                   1.539
Prob(Omnibus):                  0.000   Jarque-Bera (JB):             1138.404
Skew:                           2.233   Prob(JB):                    6.29e-248
Kurtosis:                      13.770   Cond. No.                         254.
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

In [ ]:
from statsmodels.iolib.summary2 import summary_col
info_dict={'R-squared' : lambda x: f"{x.rsquared:.2f}",
           'No. observations' : lambda x: f"{int(x.nobs):d}"}
TMwage_Out = summary_col(TMwage_lm,info_dict = info_dict)
print(TMwage_Out)


                  TMValue 
--------------------------
Intercept        -75.9393 
                 (10.5048)
wages            2.6173   
                 (0.0786) 
R-squared        0.8477   
R-squared Adj.   0.8470   
R-squared        0.85     
No. observations 201      
Standard errors in
parentheses.


In [ ]:
TM2011 = TMdatNoZero[TMdatNoZero.seasonyrend == 2011]
TM2012 = TMdatNoZero[TMdatNoZero.seasonyrend == 2012]
TM2013 = TMdatNoZero[TMdatNoZero.seasonyrend == 2013]
TM2014 = TMdatNoZero[TMdatNoZero.seasonyrend == 2014]
TM2015 = TMdatNoZero[TMdatNoZero.seasonyrend == 2015]
TM2016 = TMdatNoZero[TMdatNoZero.seasonyrend == 2016]
TM2017 = TMdatNoZero[TMdatNoZero.seasonyrend == 2017]
TM2018 = TMdatNoZero[TMdatNoZero.seasonyrend == 2018]
TM2019 = TMdatNoZero[TMdatNoZero.seasonyrend == 2019]
TM2020 = TMdatNoZero[TMdatNoZero.seasonyrend == 2020]
TM2021 = TMdatNoZero[TMdatNoZero.seasonyrend == 2021]

TM2011_lm = smf.ols(formula = 'TMValue ~ wages', data=TM2011).fit()
TM2012_lm = smf.ols(formula = 'TMValue ~ wages', data=TM2012).fit()
TM2013_lm = smf.ols(formula = 'TMValue ~ wages', data=TM2013).fit()
TM2014_lm = smf.ols(formula = 'TMValue ~ wages', data=TM2014).fit()
TM2015_lm = smf.ols(formula = 'TMValue ~ wages', data=TM2015).fit()
TM2016_lm = smf.ols(formula = 'TMValue ~ wages', data=TM2016).fit()
TM2017_lm = smf.ols(formula = 'TMValue ~ wages', data=TM2017).fit()
TM2018_lm = smf.ols(formula = 'TMValue ~ wages', data=TM2018).fit()
TM2019_lm = smf.ols(formula = 'TMValue ~ wages', data=TM2019).fit()
TM2020_lm = smf.ols(formula = 'TMValue ~ wages', data=TM2020).fit()
TM2021_lm = smf.ols(formula = 'TMValue ~ wages', data=TM2021).fit()

AllTM = ["All",'2011','2012','2013','2014','2015','2016','2017','2018','2019','2020','2021']

TMAll_Out = summary_col([TMwage_lm,TM2011_lm, TM2012_lm,TM2013_lm, TM2014_lm,TM2015_lm,TM2016_lm, TM2017_lm,TM2018_lm,TM2019_lm,TM2020_lm,TM2021_lm],\
                        model_names = AllTM, stars=True, info_dict = info_dict)

print(TMAll_Out)


                     All        2011      2012        2013       2014        2015       2016       2017       2018        2019       2020    2021 
--------------------------------------------------------------------------------------------------------------------------------------------------
Intercept        -75.9393*** -16.0649  -41.9445** -51.8969*** -42.3952** -55.7933*** -24.8110  -76.4519*** -72.4432** -106.9303** -94.0925  0.0177
                 (10.5048)   (13.9340) (14.6265)  (13.5827)   (16.9183)  (14.2330)   (21.0048) (22.2210)   (29.6730)  (44.7098)   (59.9644) (inf) 
wages            2.6173***   2.0355*** 2.3286***  2.2880***   2.1202***  2.2213***   1.9026*** 2.3548***   2.2253***  3.0915***   3.1931*** 3.5545
                 (0.0786)    (0.1507)  (0.1541)   (0.1303)    (0.1550)   (0.1228)    (0.1683)  (0.1574)    (0.1857)   (0.2546)    (0.3368)  (inf) 
R-squared        0.8477      0.9102    0.9270     0.9448      0.9123     0.9478      0.8766    0.9256      0.8886    

/usr/local/lib/python3.7/dist-packages/statsmodels/regression/linear_model.py:1673: RuntimeWarning:

divide by zero encountered in double_scalars

/usr/local/lib/python3.7/dist-packages/statsmodels/regression/linear_model.py:1738: RuntimeWarning:

divide by zero encountered in double_scalars

/usr/local/lib/python3.7/dist-packages/statsmodels/regression/linear_model.py:1751: RuntimeWarning:

invalid value encountered in true_divide



In [ ]:
TMwage_lm = smf.ols(formula = 'TMValue ~ Position', data=TMdatNoZero).fit()
TMwage_lm.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                TMValue   R-squared:                       0.417
Model:                            OLS   Adj. R-squared:                  0.414
Method:                 Least Squares   F-statistic:                     142.6
Date:                Tue, 14 Dec 2021   Prob (F-statistic):           3.91e-25
Time:                        08:42:23   Log-Likelihood:                -1296.0
No. Observations:                 201   AIC:                             2596.
Df Residuals:                     199   BIC:                             2603.
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept    456.6493     22.493     20.302      0.000     412.294     501.005
Position     -22.4577      1.881    -11.941      0.000     -26.166     -18.749
==============================================================================
Omnibus:                       75.363   Durbin-Watson:                   1.200
Prob(Omnibus):                  0.000   Jarque-Bera (JB):              225.386
Skew:                           1.583   Prob(JB):                     1.14e-49
Kurtosis:                       7.109   Cond. No.                         25.0
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

In [ ]:
TMwage_lm = smf.ols(formula = 'wages ~ Position', data=TMdatNoZero).fit()
TMwage_lm.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                  wages   R-squared:                       0.469
Model:                            OLS   Adj. R-squared:                  0.466
Method:                 Least Squares   F-statistic:                     175.9
Date:                Tue, 14 Dec 2021   Prob (F-statistic):           3.55e-29
Time:                        08:42:23   Log-Likelihood:                -1076.7
No. Observations:                 201   AIC:                             2157.
Df Residuals:                     199   BIC:                             2164.
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept    201.3382      7.553     26.655      0.000     186.443     216.233
Position      -8.3754      0.632    -13.261      0.000      -9.621      -7.130
==============================================================================
Omnibus:                       13.130   Durbin-Watson:                   1.280
Prob(Omnibus):                  0.001   Jarque-Bera (JB):               13.762
Skew:                           0.598   Prob(JB):                      0.00103
Kurtosis:                       3.459   Cond. No.                         25.0
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

In [ ]:
gbygdat = pd.read_excel("EPL game results 2011-21 with odds.xlsx")
gbygdat

seasonyrend          home_team       away_team  ...  B365H  B365D B365A
0            2011        Aston Villa         Arsenal  ...   3.40   3.30  2.20
1            2011    Birmingham City         Arsenal  ...   5.50   3.60  1.67
2            2011   Blackburn Rovers         Arsenal  ...   6.00   4.00  1.57
3            2011          Blackpool         Arsenal  ...   8.50   5.00  1.36
4            2011   Bolton Wanderers         Arsenal  ...   4.50   3.80  1.75
...           ...                ...             ...  ...    ...    ...   ...
4324         2022       Leeds United       Brentford  ...   1.95   3.60  3.80
4325         2022  Manchester United  Crystal Palace  ...   1.50   4.33  6.50
4326         2022  Tottenham Hotspur    Norwich City  ...   1.36   5.00  8.50
4327         2022        Aston Villa  Leicester City  ...   2.37   3.40  3.00
4328         2022            Everton         Arsenal  ...   3.40   3.50  2.10

[4329 rows x 9 columns]

In [ ]:
gbygdat.shape

(4329, 9)

In [ ]:
gbygdat['B365HPr']= 1/(gbygdat['B365H'])/(1/(gbygdat['B365H'])+ 1/(gbygdat['B365D'])+ 1/(gbygdat['B365A']))
gbygdat['B365DPr']= 1/(gbygdat['B365D'])/(1/(gbygdat['B365H'])+ 1/(gbygdat['B365D'])+ 1/(gbygdat['B365A']))
gbygdat['B365APr']= 1/(gbygdat['B365A'])/(1/(gbygdat['B365H'])+ 1/(gbygdat['B365D'])+ 1/(gbygdat['B365A']))
gbygdat.head()

seasonyrend         home_team away_team  ...   B365HPr   B365DPr   B365APr
0         2011       Aston Villa   Arsenal  ...  0.279661  0.288136  0.432203
1         2011   Birmingham City   Arsenal  ...  0.171786  0.262451  0.565763
2         2011  Blackburn Rovers   Arsenal  ...  0.158186  0.237280  0.604534
3         2011         Blackpool   Arsenal  ...  0.111732  0.189944  0.698324
4         2011  Bolton Wanderers   Arsenal  ...  0.210277  0.249012  0.540711

[5 rows x 12 columns]

In [ ]:
gbygdat['B365res']= np.where((gbygdat['B365HPr']>gbygdat['B365DPr']) & (gbygdat['B365HPr']>gbygdat['B365APr']),'H',\
                            np.where((gbygdat['B365DPr']>gbygdat['B365HPr']) & (gbygdat['B365DPr']>gbygdat['B365APr']),'D','A'))
gbygdat.head()

seasonyrend         home_team away_team  ...   B365DPr   B365APr B365res
0         2011       Aston Villa   Arsenal  ...  0.288136  0.432203       A
1         2011   Birmingham City   Arsenal  ...  0.262451  0.565763       A
2         2011  Blackburn Rovers   Arsenal  ...  0.237280  0.604534       A
3         2011         Blackpool   Arsenal  ...  0.189944  0.698324       A
4         2011  Bolton Wanderers   Arsenal  ...  0.249012  0.540711       A

[5 rows x 13 columns]

In [ ]:
gbygdat['B365true']= np.where(gbygdat['B365res'] == gbygdat['FTR'],1,0)
gbygdat['B365true'].mean()

0.541002541002541

In [ ]:
gbygdat['Houtcome']= np.where(gbygdat['FTR']=='H',1,0)
gbygdat['Doutcome']= np.where(gbygdat['FTR']=='D',1,0)
gbygdat['Aoutcome']= np.where(gbygdat['FTR']=='A',1,0)
gbygdat

seasonyrend          home_team  ... Doutcome  Aoutcome
0            2011        Aston Villa  ...        0         1
1            2011    Birmingham City  ...        0         1
2            2011   Blackburn Rovers  ...        0         1
3            2011          Blackpool  ...        0         1
4            2011   Bolton Wanderers  ...        0         0
...           ...                ...  ...      ...       ...
4324         2022       Leeds United  ...        1         0
4325         2022  Manchester United  ...        0         0
4326         2022  Tottenham Hotspur  ...        0         0
4327         2022        Aston Villa  ...        0         0
4328         2022            Everton  ...        0         0

[4329 rows x 17 columns]

In [ ]:
BrierB365 = ((gbygdat['B365HPr'] - gbygdat['Houtcome'])**2 +(gbygdat['B365DPr'] - gbygdat['Doutcome'])**2 +\
             (gbygdat['B365APr'] - gbygdat['Aoutcome'])**2).sum()/4329
BrierB365

0.5719074219354464

In [ ]:
# first we create the merge id in gbygdat

gbygdat['hteamid'] = gbygdat['home_team']+gbygdat['seasonyrend'].map(str)
gbygdat['ateamid'] = gbygdat['away_team']+gbygdat['seasonyrend'].map(str)

gbygdat

seasonyrend          home_team  ...                hteamid             ateamid
0            2011        Aston Villa  ...        Aston Villa2011         Arsenal2011
1            2011    Birmingham City  ...    Birmingham City2011         Arsenal2011
2            2011   Blackburn Rovers  ...   Blackburn Rovers2011         Arsenal2011
3            2011          Blackpool  ...          Blackpool2011         Arsenal2011
4            2011   Bolton Wanderers  ...   Bolton Wanderers2011         Arsenal2011
...           ...                ...  ...                    ...                 ...
4324         2022       Leeds United  ...       Leeds United2022       Brentford2022
4325         2022  Manchester United  ...  Manchester United2022  Crystal Palace2022
4326         2022  Tottenham Hotspur  ...  Tottenham Hotspur2022    Norwich City2022
4327         2022        Aston Villa  ...        Aston Villa2022  Leicester City2022
4328         2022            Everton  ...            Everton2022         Arsenal2022

[4329 rows x 19 columns]

In [ ]:
TMdat = pd.read_excel("Latest 22 - EPL TM values 2010-11 to 2021-22.xlsx")

In [ ]:
TMdat['hteamid'] = TMdat['Club']+TMdat['seasonyrend'].astype(str)
TMdat['ateamid'] = TMdat['Club']+TMdat['seasonyrend'].astype(str)

TMdat

seasonyrbegin  seasonyrend  ...               hteamid               ateamid
0             2010         2011  ...           Arsenal2011           Arsenal2011
1             2010         2011  ...       Aston Villa2011       Aston Villa2011
2             2010         2011  ...   Birmingham City2011   Birmingham City2011
3             2010         2011  ...  Blackburn Rovers2011  Blackburn Rovers2011
4             2010         2011  ...         Blackpool2011         Blackpool2011
..             ...          ...  ...                   ...                   ...
235           2021         2022  ...  Newcastle United2022  Newcastle United2022
236           2021         2022  ...         Brentford2022         Brentford2022
237           2021         2022  ...      Norwich City2022      Norwich City2022
238           2021         2022  ...           Watford2022           Watford2022
239           2021         2022  ...           Burnley2022           Burnley2022

[240 rows x 6 columns]

In [ ]:
gbygdat = pd.merge(gbygdat,TMdat[['hteamid','TMValue']], on= 'hteamid', how = 'left').rename(columns={'TMValue':'hTM'})
gbygdat

seasonyrend          home_team  ...             ateamid     hTM
0            2011        Aston Villa  ...         Arsenal2011  127.94
1            2011    Birmingham City  ...         Arsenal2011   68.00
2            2011   Blackburn Rovers  ...         Arsenal2011   65.93
3            2011          Blackpool  ...         Arsenal2011   24.37
4            2011   Bolton Wanderers  ...         Arsenal2011   74.93
...           ...                ...  ...                 ...     ...
4324         2022       Leeds United  ...       Brentford2022  232.83
4325         2022  Manchester United  ...  Crystal Palace2022  820.13
4326         2022  Tottenham Hotspur  ...    Norwich City2022  627.53
4327         2022        Aston Villa  ...  Leicester City2022  371.79
4328         2022            Everton  ...         Arsenal2022  385.88

[4329 rows x 20 columns]

In [ ]:
gbygdat = pd.merge(gbygdat,TMdat[['ateamid','TMValue']], on= 'ateamid', how = 'left').rename(columns={'TMValue':'aTM'})
gbygdat

seasonyrend          home_team  ...     hTM     aTM
0            2011        Aston Villa  ...  127.94  272.70
1            2011    Birmingham City  ...   68.00  272.70
2            2011   Blackburn Rovers  ...   65.93  272.70
3            2011          Blackpool  ...   24.37  272.70
4            2011   Bolton Wanderers  ...   74.93  272.70
...           ...                ...  ...     ...     ...
4324         2022       Leeds United  ...  232.83  179.96
4325         2022  Manchester United  ...  820.13  224.51
4326         2022  Tottenham Hotspur  ...  627.53  167.81
4327         2022        Aston Villa  ...  371.79  493.29
4328         2022            Everton  ...  385.88  507.15

[4329 rows x 21 columns]

In [ ]:
gbygdat['lhTMratio'] = np.log(gbygdat['hTM']/gbygdat['aTM'])
gbygdat

seasonyrend          home_team       away_team  ...     hTM     aTM lhTMratio
0            2011        Aston Villa         Arsenal  ...  127.94  272.70 -0.756811
1            2011    Birmingham City         Arsenal  ...   68.00  272.70 -1.388865
2            2011   Blackburn Rovers         Arsenal  ...   65.93  272.70 -1.419779
3            2011          Blackpool         Arsenal  ...   24.37  272.70 -2.415019
4            2011   Bolton Wanderers         Arsenal  ...   74.93  272.70 -1.291818
...           ...                ...             ...  ...     ...     ...       ...
4324         2022       Leeds United       Brentford  ...  232.83  179.96  0.257574
4325         2022  Manchester United  Crystal Palace  ...  820.13  224.51  1.295543
4326         2022  Tottenham Hotspur    Norwich City  ...  627.53  167.81  1.318959
4327         2022        Aston Villa  Leicester City  ...  371.79  493.29 -0.282768
4328         2022            Everton         Arsenal  ...  385.88  507.15 -0.273280

[4329 rows x 22 columns]

In [ ]:
gbygdat['winvalue'] = np.where(gbygdat['FTR'] == 'H', 2 ,(np.where(gbygdat['FTR'] == 'D', 1, 0)))
gbygdat

seasonyrend          home_team  ... lhTMratio  winvalue
0            2011        Aston Villa  ... -0.756811         0
1            2011    Birmingham City  ... -1.388865         0
2            2011   Blackburn Rovers  ... -1.419779         0
3            2011          Blackpool  ... -2.415019         0
4            2011   Bolton Wanderers  ... -1.291818         2
...           ...                ...  ...       ...       ...
4324         2022       Leeds United  ...  0.257574         1
4325         2022  Manchester United  ...  1.295543         2
4326         2022  Tottenham Hotspur  ...  1.318959         2
4327         2022        Aston Villa  ... -0.282768         2
4328         2022            Everton  ... -0.273280         2

[4329 rows x 23 columns]

In [ ]:
gbygdat= gbygdat.drop(columns= ['seasonyrend', 'home_team', 'away_team','B365H','B365D','B365A'])
gbygdat

FTHG  FTAG FTR   B365HPr  ...     hTM     aTM lhTMratio  winvalue
0        2     4   A  0.279661  ...  127.94  272.70 -0.756811         0
1        0     3   A  0.171786  ...   68.00  272.70 -1.388865         0
2        1     2   A  0.158186  ...   65.93  272.70 -1.419779         0
3        1     3   A  0.111732  ...   24.37  272.70 -2.415019         0
4        2     1   H  0.210277  ...   74.93  272.70 -1.291818         2
...    ...   ...  ..       ...  ...     ...     ...       ...       ...
4324     2     2   D  0.486660  ...  232.83  179.96  0.257574         1
4325     1     0   H  0.634039  ...  820.13  224.51  1.295543         2
4326     3     0   H  0.698324  ...  627.53  167.81  1.318959         2
4327     2     1   H  0.402081  ...  371.79  493.29 -0.282768         2
4328     2     1   H  0.278515  ...  385.88  507.15 -0.273280         2

[4329 rows x 17 columns]

In [ ]:
pip install scipy 

In [ ]:
pip install patsy 

In [ ]:
pip install git+https://github.com/mfschmidt/PyGEST.git

  Cloning https://github.com/mfschmidt/PyGEST.git to /tmp/pip-req-build-k2pgb7pu
  Running command git clone -q https://github.com/mfschmidt/PyGEST.git /tmp/pip-req-build-k2pgb7pu


In [ ]:
pip install git+https://github.com/statsmodels/statsmodels

  Cloning https://github.com/statsmodels/statsmodels to /tmp/pip-req-build-3rwovb1y
  Running command git clone -q https://github.com/statsmodels/statsmodels /tmp/pip-req-build-3rwovb1y
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done


In [ ]:
import numpy as np
import pandas as pd
import scipy.stats as stats

from statsmodels.miscmodels.ordinal_model import OrderedModel

In [ ]:
gbygdatMod = gbygdat.dropna(inplace=False)
gbygdatMod.shape

(4329, 17)

In [ ]:
ol = OrderedModel(gbygdatMod.winvalue, gbygdatMod.lhTMratio, distr='logit')

In [ ]:
res_log = ol.fit(method='bfgs', disp=False)
res_log.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                             OrderedModel Results                             
==============================================================================
Dep. Variable:               winvalue   Log-Likelihood:                -4276.7
Model:                   OrderedModel   AIC:                             8559.
Method:            Maximum Likelihood   BIC:                             8578.
Date:                Tue, 14 Dec 2021                                         
Time:                        08:44:23                                         
No. Observations:                4329                                         
Df Residuals:                    4326                                         
Df Model:                           3                                         
==============================================================================
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
lhTMratio      0.7515      0.031     24.593      0.000       0.692       0.811
0/1           -0.9250      0.035    -26.237      0.000      -0.994      -0.856
1/2            0.1528      0.028      5.445      0.000       0.098       0.208
==============================================================================
"""

In [ ]:
res_log.params

lhTMratio    0.751540
0/1         -0.925008
1/2          0.152764
dtype: float64

In [ ]:
gbygdat['predA'] = 1/(1+np.exp(-(res_log.params[1]-res_log.params[0]*gbygdat['lhTMratio'])))
gbygdat['predD'] = 1/(1+np.exp(-(res_log.params[2]-res_log.params[0]*gbygdat['lhTMratio']))) - gbygdat['predA']
gbygdat['predH'] = 1 - gbygdat['predA'] - gbygdat['predD']

gbygdat

FTHG  FTAG FTR   B365HPr  ...  winvalue     predA     predD     predH
0        2     4   A  0.279661  ...         0  0.411871  0.261074  0.327054
1        0     3   A  0.171786  ...         0  0.529660  0.238251  0.232089
2        1     2   A  0.158186  ...         0  0.535444  0.236582  0.227974
3        1     3   A  0.111732  ...         0  0.708885  0.168484  0.122631
4        2     1   H  0.210277  ...         2  0.511459  0.243200  0.245341
...    ...   ...  ..       ...  ...       ...       ...       ...       ...
4324     2     2   D  0.486660  ...         1  0.246274  0.243524  0.510202
4325     1     0   H  0.634039  ...         2  0.130260  0.175315  0.694425
4326     3     0   H  0.698324  ...         2  0.128279  0.173574  0.698146
4327     2     1   H  0.402081  ...         2  0.329048  0.261269  0.409683
4328     2     1   H  0.278515  ...         2  0.327475  0.261116  0.411409

[4329 rows x 20 columns]

In [ ]:
gbygdat['Maxprob'] =gbygdat[['predA','predD','predH']].max(axis=1)
pd.set_option('display.max_columns', 30)
gbygdat

FTHG  FTAG FTR   B365HPr   B365DPr   B365APr B365res  B365true  \
0        2     4   A  0.279661  0.288136  0.432203       A         1   
1        0     3   A  0.171786  0.262451  0.565763       A         1   
2        1     2   A  0.158186  0.237280  0.604534       A         1   
3        1     3   A  0.111732  0.189944  0.698324       A         1   
4        2     1   H  0.210277  0.249012  0.540711       A         0   
...    ...   ...  ..       ...       ...       ...     ...       ...   
4324     2     2   D  0.486660  0.263607  0.249733       H         0   
4325     1     0   H  0.634039  0.219644  0.146317       H         1   
4326     3     0   H  0.698324  0.189944  0.111732       H         1   
4327     2     1   H  0.402081  0.280274  0.317644       H         1   
4328     2     1   H  0.278515  0.270557  0.450928       A         0   

      Houtcome  Doutcome  Aoutcome                hteamid             ateamid  \
0            0         0         1        Aston Villa2011         Arsenal2011   
1            0         0         1    Birmingham City2011         Arsenal2011   
2            0         0         1   Blackburn Rovers2011         Arsenal2011   
3            0         0         1          Blackpool2011         Arsenal2011   
4            1         0         0   Bolton Wanderers2011         Arsenal2011   
...        ...       ...       ...                    ...                 ...   
4324         0         1         0       Leeds United2022       Brentford2022   
4325         1         0         0  Manchester United2022  Crystal Palace2022   
4326         1         0         0  Tottenham Hotspur2022    Norwich City2022   
4327         1         0         0        Aston Villa2022  Leicester City2022   
4328         1         0         0            Everton2022         Arsenal2022   

         hTM     aTM  lhTMratio  winvalue     predA     predD     predH  \
0     127.94  272.70  -0.756811         0  0.411871  0.261074  0.327054   
1      68.00  272.70  -1.388865         0  0.529660  0.238251  0.232089   
2      65.93  272.70  -1.419779         0  0.535444  0.236582  0.227974   
3      24.37  272.70  -2.415019         0  0.708885  0.168484  0.122631   
4      74.93  272.70  -1.291818         2  0.511459  0.243200  0.245341   
...      ...     ...        ...       ...       ...       ...       ...   
4324  232.83  179.96   0.257574         1  0.246274  0.243524  0.510202   
4325  820.13  224.51   1.295543         2  0.130260  0.175315  0.694425   
4326  627.53  167.81   1.318959         2  0.128279  0.173574  0.698146   
4327  371.79  493.29  -0.282768         2  0.329048  0.261269  0.409683   
4328  385.88  507.15  -0.273280         2  0.327475  0.261116  0.411409   

       Maxprob  
0     0.411871  
1     0.529660  
2     0.535444  
3     0.708885  
4     0.511459  
...        ...  
4324  0.510202  
4325  0.694425  
4326  0.698146  
4327  0.409683  
4328  0.411409  

[4329 rows x 21 columns]

In [ ]:
# the predicted result

gbygdat['logitpred']=np.where(gbygdat['Maxprob']==gbygdat['predA'],'A',np.where(gbygdat['Maxprob']==gbygdat['predD'],'D','H'))
gbygdat

FTHG  FTAG FTR   B365HPr   B365DPr   B365APr B365res  B365true  \
0        2     4   A  0.279661  0.288136  0.432203       A         1   
1        0     3   A  0.171786  0.262451  0.565763       A         1   
2        1     2   A  0.158186  0.237280  0.604534       A         1   
3        1     3   A  0.111732  0.189944  0.698324       A         1   
4        2     1   H  0.210277  0.249012  0.540711       A         0   
...    ...   ...  ..       ...       ...       ...     ...       ...   
4324     2     2   D  0.486660  0.263607  0.249733       H         0   
4325     1     0   H  0.634039  0.219644  0.146317       H         1   
4326     3     0   H  0.698324  0.189944  0.111732       H         1   
4327     2     1   H  0.402081  0.280274  0.317644       H         1   
4328     2     1   H  0.278515  0.270557  0.450928       A         0   

      Houtcome  Doutcome  Aoutcome                hteamid             ateamid  \
0            0         0         1        Aston Villa2011         Arsenal2011   
1            0         0         1    Birmingham City2011         Arsenal2011   
2            0         0         1   Blackburn Rovers2011         Arsenal2011   
3            0         0         1          Blackpool2011         Arsenal2011   
4            1         0         0   Bolton Wanderers2011         Arsenal2011   
...        ...       ...       ...                    ...                 ...   
4324         0         1         0       Leeds United2022       Brentford2022   
4325         1         0         0  Manchester United2022  Crystal Palace2022   
4326         1         0         0  Tottenham Hotspur2022    Norwich City2022   
4327         1         0         0        Aston Villa2022  Leicester City2022   
4328         1         0         0            Everton2022         Arsenal2022   

         hTM     aTM  lhTMratio  winvalue     predA     predD     predH  \
0     127.94  272.70  -0.756811         0  0.411871  0.261074  0.327054   
1      68.00  272.70  -1.388865         0  0.529660  0.238251  0.232089   
2      65.93  272.70  -1.419779         0  0.535444  0.236582  0.227974   
3      24.37  272.70  -2.415019         0  0.708885  0.168484  0.122631   
4      74.93  272.70  -1.291818         2  0.511459  0.243200  0.245341   
...      ...     ...        ...       ...       ...       ...       ...   
4324  232.83  179.96   0.257574         1  0.246274  0.243524  0.510202   
4325  820.13  224.51   1.295543         2  0.130260  0.175315  0.694425   
4326  627.53  167.81   1.318959         2  0.128279  0.173574  0.698146   
4327  371.79  493.29  -0.282768         2  0.329048  0.261269  0.409683   
4328  385.88  507.15  -0.273280         2  0.327475  0.261116  0.411409   

       Maxprob logitpred  
0     0.411871         A  
1     0.529660         A  
2     0.535444         A  
3     0.708885         A  
4     0.511459         A  
...        ...       ...  
4324  0.510202         H  
4325  0.694425         H  
4326  0.698146         H  
4327  0.409683         H  
4328  0.411409         H  

[4329 rows x 22 columns]

In [ ]:
gbygdat['logittrue']= np.where(gbygdat['logitpred'] == gbygdat['FTR'],1,0)
gbygdat

FTHG  FTAG FTR   B365HPr   B365DPr   B365APr B365res  B365true  \
0        2     4   A  0.279661  0.288136  0.432203       A         1   
1        0     3   A  0.171786  0.262451  0.565763       A         1   
2        1     2   A  0.158186  0.237280  0.604534       A         1   
3        1     3   A  0.111732  0.189944  0.698324       A         1   
4        2     1   H  0.210277  0.249012  0.540711       A         0   
...    ...   ...  ..       ...       ...       ...     ...       ...   
4324     2     2   D  0.486660  0.263607  0.249733       H         0   
4325     1     0   H  0.634039  0.219644  0.146317       H         1   
4326     3     0   H  0.698324  0.189944  0.111732       H         1   
4327     2     1   H  0.402081  0.280274  0.317644       H         1   
4328     2     1   H  0.278515  0.270557  0.450928       A         0   

      Houtcome  Doutcome  Aoutcome                hteamid             ateamid  \
0            0         0         1        Aston Villa2011         Arsenal2011   
1            0         0         1    Birmingham City2011         Arsenal2011   
2            0         0         1   Blackburn Rovers2011         Arsenal2011   
3            0         0         1          Blackpool2011         Arsenal2011   
4            1         0         0   Bolton Wanderers2011         Arsenal2011   
...        ...       ...       ...                    ...                 ...   
4324         0         1         0       Leeds United2022       Brentford2022   
4325         1         0         0  Manchester United2022  Crystal Palace2022   
4326         1         0         0  Tottenham Hotspur2022    Norwich City2022   
4327         1         0         0        Aston Villa2022  Leicester City2022   
4328         1         0         0            Everton2022         Arsenal2022   

         hTM     aTM  lhTMratio  winvalue     predA     predD     predH  \
0     127.94  272.70  -0.756811         0  0.411871  0.261074  0.327054   
1      68.00  272.70  -1.388865         0  0.529660  0.238251  0.232089   
2      65.93  272.70  -1.419779         0  0.535444  0.236582  0.227974   
3      24.37  272.70  -2.415019         0  0.708885  0.168484  0.122631   
4      74.93  272.70  -1.291818         2  0.511459  0.243200  0.245341   
...      ...     ...        ...       ...       ...       ...       ...   
4324  232.83  179.96   0.257574         1  0.246274  0.243524  0.510202   
4325  820.13  224.51   1.295543         2  0.130260  0.175315  0.694425   
4326  627.53  167.81   1.318959         2  0.128279  0.173574  0.698146   
4327  371.79  493.29  -0.282768         2  0.329048  0.261269  0.409683   
4328  385.88  507.15  -0.273280         2  0.327475  0.261116  0.411409   

       Maxprob logitpred  logittrue  
0     0.411871         A          1  
1     0.529660         A          1  
2     0.535444         A          1  
3     0.708885         A          1  
4     0.511459         A          0  
...        ...       ...        ...  
4324  0.510202         H          0  
4325  0.694425         H          1  
4326  0.698146         H          1  
4327  0.409683         H          1  
4328  0.411409         H          1  

[4329 rows x 23 columns]

In [ ]:
gbygdat['logittrue'].mean()

0.5239085239085239

In [ ]:
Brierlogit = ((gbygdat['predH'] - gbygdat['Houtcome'])**2 +(gbygdat['predD'] - gbygdat['Doutcome'])**2 +\
             (gbygdat['predA'] - gbygdat['Aoutcome'])**2).sum()/4329
Brierlogit

0.5888172766705541

In [ ]:
#same prediction

samepercent = np.where(gbygdat['B365res'] == gbygdat['logitpred'],1,0).sum()/4329
samepercent

0.8731808731808732

In [ ]:
season21_22 = pd.read_excel('2022 spi_matches_latest.xlsx')
TM_21_22 = pd.read_excel('EPL TM values 2021-22.xlsx')
bet365_odds_22 = pd.read_excel('EPL game results 2022 with odds.xlsx')

In [ ]:
TM_21_22

seasonyrbegin  seasonyrend                     Club  TMValue
0            2021         2022          Manchester City   970.02
1            2021         2022        Manchester United   820.13
2            2021         2022                  Chelsea   802.35
3            2021         2022                Liverpool   779.85
4            2021         2022        Tottenham Hotspur   627.53
5            2021         2022                  Arsenal   507.15
6            2021         2022           Leicester City   493.29
7            2021         2022                  Everton   385.88
8            2021         2022              Aston Villa   371.79
9            2021         2022  Wolverhampton Wanderers   345.69
10           2021         2022          West Ham United   318.83
11           2021         2022             Leeds United   232.83
12           2021         2022   Brighton & Hove Albion   231.30
13           2021         2022              Southampton   229.91
14           2021         2022           Crystal Palace   224.51
15           2021         2022         Newcastle United   220.86
16           2021         2022                Brentford   179.96
17           2021         2022             Norwich City   167.81
18           2021         2022                  Watford   130.95
19           2021         2022                  Burnley   130.77

In [ ]:
season21_22

season       date  league_id                   league          Home team  \
0      2022 2021-08-13       2411  Barclays Premier League          Brentford   
1      2022 2021-08-14       2411  Barclays Premier League  Manchester United   
2      2022 2021-08-14       2411  Barclays Premier League     Leicester City   
3      2022 2021-08-14       2411  Barclays Premier League            Everton   
4      2022 2021-08-14       2411  Barclays Premier League            Chelsea   
..      ...        ...        ...                      ...                ...   
375    2022 2022-05-22       2411  Barclays Premier League            Chelsea   
376    2022 2022-05-22       2411  Barclays Premier League    Manchester City   
377    2022 2022-05-22       2411  Barclays Premier League            Burnley   
378    2022 2022-05-22       2411  Barclays Premier League     Leicester City   
379    2022 2022-05-22       2411  Barclays Premier League            Arsenal   

                   Away team  538hpr  538apr  538dpr  FTHG  FTAG  FTR  month  \
0                    Arsenal  0.2240  0.5209  0.2552   2.0   0.0    H      8   
1               Leeds United  0.6282  0.1622  0.2096   5.0   1.0    H      8   
2    Wolverhampton Wanderers  0.5333  0.2155  0.2512   1.0   0.0    H      8   
3                Southampton  0.4789  0.2624  0.2587   3.0   1.0    H      8   
4             Crystal Palace  0.7531  0.0769  0.1700   3.0   0.0    H      8   
..                       ...     ...     ...     ...   ...   ...  ...    ...   
375                  Watford  0.7554  0.0842  0.1604   NaN   NaN  NaN      5   
376              Aston Villa  0.7473  0.0929  0.1598   NaN   NaN  NaN      5   
377         Newcastle United  0.4675  0.2790  0.2536   NaN   NaN  NaN      5   
378              Southampton  0.4624  0.2904  0.2473   NaN   NaN  NaN      5   
379                  Everton  0.4921  0.2503  0.2576   NaN   NaN  NaN      5   

     day  year  notplayed  
0     13  2021          0  
1     14  2021          0  
2     14  2021          0  
3     14  2021          0  
4     14  2021          0  
..   ...   ...        ...  
375   22  2022          1  
376   22  2022          1  
377   22  2022          1  
378   22  2022          1  
379   22  2022          1  

[380 rows x 16 columns]

In [ ]:
# first we create the merge id in gbygdat

season21_22['hteamid'] = season21_22['Home team']+season21_22['season'].map(str)
season21_22['ateamid'] = season21_22['Away team']+season21_22['season'].map(str)

season21_22

season       date  league_id                   league          Home team  \
0      2022 2021-08-13       2411  Barclays Premier League          Brentford   
1      2022 2021-08-14       2411  Barclays Premier League  Manchester United   
2      2022 2021-08-14       2411  Barclays Premier League     Leicester City   
3      2022 2021-08-14       2411  Barclays Premier League            Everton   
4      2022 2021-08-14       2411  Barclays Premier League            Chelsea   
..      ...        ...        ...                      ...                ...   
375    2022 2022-05-22       2411  Barclays Premier League            Chelsea   
376    2022 2022-05-22       2411  Barclays Premier League    Manchester City   
377    2022 2022-05-22       2411  Barclays Premier League            Burnley   
378    2022 2022-05-22       2411  Barclays Premier League     Leicester City   
379    2022 2022-05-22       2411  Barclays Premier League            Arsenal   

                   Away team  538hpr  538apr  538dpr  FTHG  FTAG  FTR  month  \
0                    Arsenal  0.2240  0.5209  0.2552   2.0   0.0    H      8   
1               Leeds United  0.6282  0.1622  0.2096   5.0   1.0    H      8   
2    Wolverhampton Wanderers  0.5333  0.2155  0.2512   1.0   0.0    H      8   
3                Southampton  0.4789  0.2624  0.2587   3.0   1.0    H      8   
4             Crystal Palace  0.7531  0.0769  0.1700   3.0   0.0    H      8   
..                       ...     ...     ...     ...   ...   ...  ...    ...   
375                  Watford  0.7554  0.0842  0.1604   NaN   NaN  NaN      5   
376              Aston Villa  0.7473  0.0929  0.1598   NaN   NaN  NaN      5   
377         Newcastle United  0.4675  0.2790  0.2536   NaN   NaN  NaN      5   
378              Southampton  0.4624  0.2904  0.2473   NaN   NaN  NaN      5   
379                  Everton  0.4921  0.2503  0.2576   NaN   NaN  NaN      5   

     day  year  notplayed                hteamid                      ateamid  
0     13  2021          0          Brentford2022                  Arsenal2022  
1     14  2021          0  Manchester United2022             Leeds United2022  
2     14  2021          0     Leicester City2022  Wolverhampton Wanderers2022  
3     14  2021          0            Everton2022              Southampton2022  
4     14  2021          0            Chelsea2022           Crystal Palace2022  
..   ...   ...        ...                    ...                          ...  
375   22  2022          1            Chelsea2022                  Watford2022  
376   22  2022          1    Manchester City2022              Aston Villa2022  
377   22  2022          1            Burnley2022         Newcastle United2022  
378   22  2022          1     Leicester City2022              Southampton2022  
379   22  2022          1            Arsenal2022                  Everton2022  

[380 rows x 18 columns]

In [ ]:
TM_21_22['hteamid'] = TM_21_22['Club']+TM_21_22['seasonyrend'].astype(str)
TM_21_22['ateamid'] = TM_21_22['Club']+TM_21_22['seasonyrend'].astype(str)

TM_21_22

seasonyrbegin  seasonyrend                     Club  TMValue  \
0            2021         2022          Manchester City   970.02   
1            2021         2022        Manchester United   820.13   
2            2021         2022                  Chelsea   802.35   
3            2021         2022                Liverpool   779.85   
4            2021         2022        Tottenham Hotspur   627.53   
5            2021         2022                  Arsenal   507.15   
6            2021         2022           Leicester City   493.29   
7            2021         2022                  Everton   385.88   
8            2021         2022              Aston Villa   371.79   
9            2021         2022  Wolverhampton Wanderers   345.69   
10           2021         2022          West Ham United   318.83   
11           2021         2022             Leeds United   232.83   
12           2021         2022   Brighton & Hove Albion   231.30   
13           2021         2022              Southampton   229.91   
14           2021         2022           Crystal Palace   224.51   
15           2021         2022         Newcastle United   220.86   
16           2021         2022                Brentford   179.96   
17           2021         2022             Norwich City   167.81   
18           2021         2022                  Watford   130.95   
19           2021         2022                  Burnley   130.77   

                        hteamid                      ateamid  
0           Manchester City2022          Manchester City2022  
1         Manchester United2022        Manchester United2022  
2                   Chelsea2022                  Chelsea2022  
3                 Liverpool2022                Liverpool2022  
4         Tottenham Hotspur2022        Tottenham Hotspur2022  
5                   Arsenal2022                  Arsenal2022  
6            Leicester City2022           Leicester City2022  
7                   Everton2022                  Everton2022  
8               Aston Villa2022              Aston Villa2022  
9   Wolverhampton Wanderers2022  Wolverhampton Wanderers2022  
10          West Ham United2022          West Ham United2022  
11             Leeds United2022             Leeds United2022  
12   Brighton & Hove Albion2022   Brighton & Hove Albion2022  
13              Southampton2022              Southampton2022  
14           Crystal Palace2022           Crystal Palace2022  
15         Newcastle United2022         Newcastle United2022  
16                Brentford2022                Brentford2022  
17             Norwich City2022             Norwich City2022  
18                  Watford2022                  Watford2022  
19                  Burnley2022                  Burnley2022

In [ ]:
season21_22 = pd.merge(season21_22,TM_21_22[['hteamid','TMValue']], on= 'hteamid', how = 'left').rename(columns={'TMValue':'TMhome'})
season21_22

season       date  league_id                   league          Home team  \
0      2022 2021-08-13       2411  Barclays Premier League          Brentford   
1      2022 2021-08-14       2411  Barclays Premier League  Manchester United   
2      2022 2021-08-14       2411  Barclays Premier League     Leicester City   
3      2022 2021-08-14       2411  Barclays Premier League            Everton   
4      2022 2021-08-14       2411  Barclays Premier League            Chelsea   
..      ...        ...        ...                      ...                ...   
375    2022 2022-05-22       2411  Barclays Premier League            Chelsea   
376    2022 2022-05-22       2411  Barclays Premier League    Manchester City   
377    2022 2022-05-22       2411  Barclays Premier League            Burnley   
378    2022 2022-05-22       2411  Barclays Premier League     Leicester City   
379    2022 2022-05-22       2411  Barclays Premier League            Arsenal   

                   Away team  538hpr  538apr  538dpr  FTHG  FTAG  FTR  month  \
0                    Arsenal  0.2240  0.5209  0.2552   2.0   0.0    H      8   
1               Leeds United  0.6282  0.1622  0.2096   5.0   1.0    H      8   
2    Wolverhampton Wanderers  0.5333  0.2155  0.2512   1.0   0.0    H      8   
3                Southampton  0.4789  0.2624  0.2587   3.0   1.0    H      8   
4             Crystal Palace  0.7531  0.0769  0.1700   3.0   0.0    H      8   
..                       ...     ...     ...     ...   ...   ...  ...    ...   
375                  Watford  0.7554  0.0842  0.1604   NaN   NaN  NaN      5   
376              Aston Villa  0.7473  0.0929  0.1598   NaN   NaN  NaN      5   
377         Newcastle United  0.4675  0.2790  0.2536   NaN   NaN  NaN      5   
378              Southampton  0.4624  0.2904  0.2473   NaN   NaN  NaN      5   
379                  Everton  0.4921  0.2503  0.2576   NaN   NaN  NaN      5   

     day  year  notplayed                hteamid                      ateamid  \
0     13  2021          0          Brentford2022                  Arsenal2022   
1     14  2021          0  Manchester United2022             Leeds United2022   
2     14  2021          0     Leicester City2022  Wolverhampton Wanderers2022   
3     14  2021          0            Everton2022              Southampton2022   
4     14  2021          0            Chelsea2022           Crystal Palace2022   
..   ...   ...        ...                    ...                          ...   
375   22  2022          1            Chelsea2022                  Watford2022   
376   22  2022          1    Manchester City2022              Aston Villa2022   
377   22  2022          1            Burnley2022         Newcastle United2022   
378   22  2022          1     Leicester City2022              Southampton2022   
379   22  2022          1            Arsenal2022                  Everton2022   

     TMhome  
0    179.96  
1    820.13  
2    493.29  
3    385.88  
4    802.35  
..      ...  
375  802.35  
376  970.02  
377  130.77  
378  493.29  
379  507.15  

[380 rows x 19 columns]

In [ ]:
season21_22 = pd.merge(season21_22,TM_21_22[['ateamid','TMValue']], on= 'ateamid', how = 'left').rename(columns={'TMValue':'TMaway'})
season21_22

season       date  league_id                   league          Home team  \
0      2022 2021-08-13       2411  Barclays Premier League          Brentford   
1      2022 2021-08-14       2411  Barclays Premier League  Manchester United   
2      2022 2021-08-14       2411  Barclays Premier League     Leicester City   
3      2022 2021-08-14       2411  Barclays Premier League            Everton   
4      2022 2021-08-14       2411  Barclays Premier League            Chelsea   
..      ...        ...        ...                      ...                ...   
375    2022 2022-05-22       2411  Barclays Premier League            Chelsea   
376    2022 2022-05-22       2411  Barclays Premier League    Manchester City   
377    2022 2022-05-22       2411  Barclays Premier League            Burnley   
378    2022 2022-05-22       2411  Barclays Premier League     Leicester City   
379    2022 2022-05-22       2411  Barclays Premier League            Arsenal   

                   Away team  538hpr  538apr  538dpr  FTHG  FTAG  FTR  month  \
0                    Arsenal  0.2240  0.5209  0.2552   2.0   0.0    H      8   
1               Leeds United  0.6282  0.1622  0.2096   5.0   1.0    H      8   
2    Wolverhampton Wanderers  0.5333  0.2155  0.2512   1.0   0.0    H      8   
3                Southampton  0.4789  0.2624  0.2587   3.0   1.0    H      8   
4             Crystal Palace  0.7531  0.0769  0.1700   3.0   0.0    H      8   
..                       ...     ...     ...     ...   ...   ...  ...    ...   
375                  Watford  0.7554  0.0842  0.1604   NaN   NaN  NaN      5   
376              Aston Villa  0.7473  0.0929  0.1598   NaN   NaN  NaN      5   
377         Newcastle United  0.4675  0.2790  0.2536   NaN   NaN  NaN      5   
378              Southampton  0.4624  0.2904  0.2473   NaN   NaN  NaN      5   
379                  Everton  0.4921  0.2503  0.2576   NaN   NaN  NaN      5   

     day  year  notplayed                hteamid                      ateamid  \
0     13  2021          0          Brentford2022                  Arsenal2022   
1     14  2021          0  Manchester United2022             Leeds United2022   
2     14  2021          0     Leicester City2022  Wolverhampton Wanderers2022   
3     14  2021          0            Everton2022              Southampton2022   
4     14  2021          0            Chelsea2022           Crystal Palace2022   
..   ...   ...        ...                    ...                          ...   
375   22  2022          1            Chelsea2022                  Watford2022   
376   22  2022          1    Manchester City2022              Aston Villa2022   
377   22  2022          1            Burnley2022         Newcastle United2022   
378   22  2022          1     Leicester City2022              Southampton2022   
379   22  2022          1            Arsenal2022                  Everton2022   

     TMhome  TMaway  
0    179.96  507.15  
1    820.13  232.83  
2    493.29  345.69  
3    385.88  229.91  
4    802.35  224.51  
..      ...     ...  
375  802.35  130.95  
376  970.02  371.79  
377  130.77  220.86  
378  493.29  229.91  
379  507.15  385.88  

[380 rows x 20 columns]

In [ ]:
# first we create the merge id in gbygdat

season21_22['bet365hateamid'] = season21_22['Home team']+season21_22['Away team']

season21_22

season       date  league_id                   league          Home team  \
0      2022 2021-08-13       2411  Barclays Premier League          Brentford   
1      2022 2021-08-14       2411  Barclays Premier League  Manchester United   
2      2022 2021-08-14       2411  Barclays Premier League     Leicester City   
3      2022 2021-08-14       2411  Barclays Premier League            Everton   
4      2022 2021-08-14       2411  Barclays Premier League            Chelsea   
..      ...        ...        ...                      ...                ...   
375    2022 2022-05-22       2411  Barclays Premier League            Chelsea   
376    2022 2022-05-22       2411  Barclays Premier League    Manchester City   
377    2022 2022-05-22       2411  Barclays Premier League            Burnley   
378    2022 2022-05-22       2411  Barclays Premier League     Leicester City   
379    2022 2022-05-22       2411  Barclays Premier League            Arsenal   

                   Away team  538hpr  538apr  538dpr  FTHG  FTAG  FTR  month  \
0                    Arsenal  0.2240  0.5209  0.2552   2.0   0.0    H      8   
1               Leeds United  0.6282  0.1622  0.2096   5.0   1.0    H      8   
2    Wolverhampton Wanderers  0.5333  0.2155  0.2512   1.0   0.0    H      8   
3                Southampton  0.4789  0.2624  0.2587   3.0   1.0    H      8   
4             Crystal Palace  0.7531  0.0769  0.1700   3.0   0.0    H      8   
..                       ...     ...     ...     ...   ...   ...  ...    ...   
375                  Watford  0.7554  0.0842  0.1604   NaN   NaN  NaN      5   
376              Aston Villa  0.7473  0.0929  0.1598   NaN   NaN  NaN      5   
377         Newcastle United  0.4675  0.2790  0.2536   NaN   NaN  NaN      5   
378              Southampton  0.4624  0.2904  0.2473   NaN   NaN  NaN      5   
379                  Everton  0.4921  0.2503  0.2576   NaN   NaN  NaN      5   

     day  year  notplayed                hteamid                      ateamid  \
0     13  2021          0          Brentford2022                  Arsenal2022   
1     14  2021          0  Manchester United2022             Leeds United2022   
2     14  2021          0     Leicester City2022  Wolverhampton Wanderers2022   
3     14  2021          0            Everton2022              Southampton2022   
4     14  2021          0            Chelsea2022           Crystal Palace2022   
..   ...   ...        ...                    ...                          ...   
375   22  2022          1            Chelsea2022                  Watford2022   
376   22  2022          1    Manchester City2022              Aston Villa2022   
377   22  2022          1            Burnley2022         Newcastle United2022   
378   22  2022          1     Leicester City2022              Southampton2022   
379   22  2022          1            Arsenal2022                  Everton2022   

     TMhome  TMaway                         bet365hateamid  
0    179.96  507.15                       BrentfordArsenal  
1    820.13  232.83          Manchester UnitedLeeds United  
2    493.29  345.69  Leicester CityWolverhampton Wanderers  
3    385.88  229.91                     EvertonSouthampton  
4    802.35  224.51                  ChelseaCrystal Palace  
..      ...     ...                                    ...  
375  802.35  130.95                         ChelseaWatford  
376  970.02  371.79             Manchester CityAston Villa  
377  130.77  220.86                BurnleyNewcastle United  
378  493.29  229.91              Leicester CitySouthampton  
379  507.15  385.88                         ArsenalEverton  

[380 rows x 21 columns]

In [ ]:
# first we create the merge id in gbygdat

bet365_odds_22['bet365hateamid'] = bet365_odds_22['home_team']+bet365_odds_22['away_team']

bet365_odds_22

seasonyrend          home_team               away_team  FTHG  FTAG FTR  \
0           2022          Brentford                 Arsenal     2     0   H   
1           2022  Manchester United            Leeds United     5     1   H   
2           2022            Burnley  Brighton & Hove Albion     1     2   A   
3           2022            Chelsea          Crystal Palace     3     0   H   
4           2022            Everton             Southampton     3     1   H   
..           ...                ...                     ...   ...   ...  ..   
144         2022       Leeds United               Brentford     2     2   D   
145         2022  Manchester United          Crystal Palace     1     0   H   
146         2022  Tottenham Hotspur            Norwich City     3     0   H   
147         2022        Aston Villa          Leicester City     2     1   H   
148         2022            Everton                 Arsenal     2     1   H   

     B365H  B365D  B365A                   bet365hateamid  
0     4.00   3.40   1.95                 BrentfordArsenal  
1     1.53   4.50   5.75    Manchester UnitedLeeds United  
2     3.10   3.10   2.45    BurnleyBrighton & Hove Albion  
3     1.25   5.75  13.00            ChelseaCrystal Palace  
4     1.90   3.50   4.00               EvertonSouthampton  
..     ...    ...    ...                              ...  
144   1.95   3.60   3.80            Leeds UnitedBrentford  
145   1.50   4.33   6.50  Manchester UnitedCrystal Palace  
146   1.36   5.00   8.50    Tottenham HotspurNorwich City  
147   2.37   3.40   3.00        Aston VillaLeicester City  
148   3.40   3.50   2.10                   EvertonArsenal  

[149 rows x 10 columns]

In [ ]:
season21_22 = pd.merge(season21_22,bet365_odds_22[['bet365hateamid','B365H','B365D','B365A']], on= 'bet365hateamid', how = 'left').rename(columns={'B365H':'B365H'})
season21_22

season       date  league_id                   league          Home team  \
0      2022 2021-08-13       2411  Barclays Premier League          Brentford   
1      2022 2021-08-14       2411  Barclays Premier League  Manchester United   
2      2022 2021-08-14       2411  Barclays Premier League     Leicester City   
3      2022 2021-08-14       2411  Barclays Premier League            Everton   
4      2022 2021-08-14       2411  Barclays Premier League            Chelsea   
..      ...        ...        ...                      ...                ...   
375    2022 2022-05-22       2411  Barclays Premier League            Chelsea   
376    2022 2022-05-22       2411  Barclays Premier League    Manchester City   
377    2022 2022-05-22       2411  Barclays Premier League            Burnley   
378    2022 2022-05-22       2411  Barclays Premier League     Leicester City   
379    2022 2022-05-22       2411  Barclays Premier League            Arsenal   

                   Away team  538hpr  538apr  538dpr  FTHG  FTAG  FTR  month  \
0                    Arsenal  0.2240  0.5209  0.2552   2.0   0.0    H      8   
1               Leeds United  0.6282  0.1622  0.2096   5.0   1.0    H      8   
2    Wolverhampton Wanderers  0.5333  0.2155  0.2512   1.0   0.0    H      8   
3                Southampton  0.4789  0.2624  0.2587   3.0   1.0    H      8   
4             Crystal Palace  0.7531  0.0769  0.1700   3.0   0.0    H      8   
..                       ...     ...     ...     ...   ...   ...  ...    ...   
375                  Watford  0.7554  0.0842  0.1604   NaN   NaN  NaN      5   
376              Aston Villa  0.7473  0.0929  0.1598   NaN   NaN  NaN      5   
377         Newcastle United  0.4675  0.2790  0.2536   NaN   NaN  NaN      5   
378              Southampton  0.4624  0.2904  0.2473   NaN   NaN  NaN      5   
379                  Everton  0.4921  0.2503  0.2576   NaN   NaN  NaN      5   

     day  year  notplayed                hteamid                      ateamid  \
0     13  2021          0          Brentford2022                  Arsenal2022   
1     14  2021          0  Manchester United2022             Leeds United2022   
2     14  2021          0     Leicester City2022  Wolverhampton Wanderers2022   
3     14  2021          0            Everton2022              Southampton2022   
4     14  2021          0            Chelsea2022           Crystal Palace2022   
..   ...   ...        ...                    ...                          ...   
375   22  2022          1            Chelsea2022                  Watford2022   
376   22  2022          1    Manchester City2022              Aston Villa2022   
377   22  2022          1            Burnley2022         Newcastle United2022   
378   22  2022          1     Leicester City2022              Southampton2022   
379   22  2022          1            Arsenal2022                  Everton2022   

     TMhome  TMaway                         bet365hateamid  B365H  B365D  \
0    179.96  507.15                       BrentfordArsenal   4.00   3.40   
1    820.13  232.83          Manchester UnitedLeeds United   1.53   4.50   
2    493.29  345.69  Leicester CityWolverhampton Wanderers   1.66   3.80   
3    385.88  229.91                     EvertonSouthampton   1.90   3.50   
4    802.35  224.51                  ChelseaCrystal Palace   1.25   5.75   
..      ...     ...                                    ...    ...    ...   
375  802.35  130.95                         ChelseaWatford    NaN    NaN   
376  970.02  371.79             Manchester CityAston Villa    NaN    NaN   
377  130.77  220.86                BurnleyNewcastle United    NaN    NaN   
378  493.29  229.91              Leicester CitySouthampton    NaN    NaN   
379  507.15  385.88                         ArsenalEverton    NaN    NaN   

     B365A  
0     1.95  
1     5.75  
2     5.25  
3     4.00  
4    13.00  
..     ...  
375    NaN  
376    NaN  
377    NaN  
378    NaN  
379    NaN  

[380 rows x 24 columns]

In [ ]:
season21_22= season21_22.drop(columns= ['league_id', 'season', 'league','hteamid','ateamid','bet365hateamid'])
season21_22

date          Home team                Away team  538hpr  538apr  \
0   2021-08-13          Brentford                  Arsenal  0.2240  0.5209   
1   2021-08-14  Manchester United             Leeds United  0.6282  0.1622   
2   2021-08-14     Leicester City  Wolverhampton Wanderers  0.5333  0.2155   
3   2021-08-14            Everton              Southampton  0.4789  0.2624   
4   2021-08-14            Chelsea           Crystal Palace  0.7531  0.0769   
..         ...                ...                      ...     ...     ...   
375 2022-05-22            Chelsea                  Watford  0.7554  0.0842   
376 2022-05-22    Manchester City              Aston Villa  0.7473  0.0929   
377 2022-05-22            Burnley         Newcastle United  0.4675  0.2790   
378 2022-05-22     Leicester City              Southampton  0.4624  0.2904   
379 2022-05-22            Arsenal                  Everton  0.4921  0.2503   

     538dpr  FTHG  FTAG  FTR  month  day  year  notplayed  TMhome  TMaway  \
0    0.2552   2.0   0.0    H      8   13  2021          0  179.96  507.15   
1    0.2096   5.0   1.0    H      8   14  2021          0  820.13  232.83   
2    0.2512   1.0   0.0    H      8   14  2021          0  493.29  345.69   
3    0.2587   3.0   1.0    H      8   14  2021          0  385.88  229.91   
4    0.1700   3.0   0.0    H      8   14  2021          0  802.35  224.51   
..      ...   ...   ...  ...    ...  ...   ...        ...     ...     ...   
375  0.1604   NaN   NaN  NaN      5   22  2022          1  802.35  130.95   
376  0.1598   NaN   NaN  NaN      5   22  2022          1  970.02  371.79   
377  0.2536   NaN   NaN  NaN      5   22  2022          1  130.77  220.86   
378  0.2473   NaN   NaN  NaN      5   22  2022          1  493.29  229.91   
379  0.2576   NaN   NaN  NaN      5   22  2022          1  507.15  385.88   

     B365H  B365D  B365A  
0     4.00   3.40   1.95  
1     1.53   4.50   5.75  
2     1.66   3.80   5.25  
3     1.90   3.50   4.00  
4     1.25   5.75  13.00  
..     ...    ...    ...  
375    NaN    NaN    NaN  
376    NaN    NaN    NaN  
377    NaN    NaN    NaN  
378    NaN    NaN    NaN  
379    NaN    NaN    NaN  

[380 rows x 18 columns]

In [ ]:
season21_22['B365res']= np.where((season21_22['B365H']<season21_22['B365D']) & (season21_22['B365H']<season21_22['B365A']),'H',\
                            np.where((season21_22['B365D']<season21_22['B365H']) & (season21_22['B365D']<season21_22['B365A']),'D',\
                                    np.where((season21_22['B365A']<season21_22['B365H']) & (season21_22['B365A']<season21_22['B365D']),'A',"")))
pd.set_option('display.max_rows', 400)
season21_22

date                Home team                Away team  538hpr  \
0   2021-08-13                Brentford                  Arsenal  0.2240   
1   2021-08-14        Manchester United             Leeds United  0.6282   
2   2021-08-14           Leicester City  Wolverhampton Wanderers  0.5333   
3   2021-08-14                  Everton              Southampton  0.4789   
4   2021-08-14                  Chelsea           Crystal Palace  0.7531   
5   2021-08-14                  Watford              Aston Villa  0.3067   
6   2021-08-14                  Burnley   Brighton & Hove Albion  0.3356   
7   2021-08-14             Norwich City                Liverpool  0.1293   
8   2021-08-15         Newcastle United          West Ham United  0.3533   
9   2021-08-15        Tottenham Hotspur          Manchester City  0.2239   
10  2021-08-21                Liverpool                  Burnley  0.7621   
11  2021-08-21             Leeds United                  Everton  0.4038   
12  2021-08-21          Manchester City             Norwich City  0.8281   
13  2021-08-21           Crystal Palace                Brentford  0.4091   
14  2021-08-21              Aston Villa         Newcastle United  0.4917   
15  2021-08-21   Brighton & Hove Albion                  Watford  0.5466   
16  2021-08-22  Wolverhampton Wanderers        Tottenham Hotspur  0.2905   
17  2021-08-22              Southampton        Manchester United  0.1837   
18  2021-08-22                  Arsenal                  Chelsea  0.2839   
19  2021-08-23          West Ham United           Leicester City  0.3961   
20  2021-08-28          Manchester City                  Arsenal  0.6898   
21  2021-08-28         Newcastle United              Southampton  0.4219   
22  2021-08-28          West Ham United           Crystal Palace  0.5911   
23  2021-08-28             Norwich City           Leicester City  0.2627   
24  2021-08-28              Aston Villa                Brentford  0.5099   
25  2021-08-28   Brighton & Hove Albion                  Everton  0.4250   
26  2021-08-28                Liverpool                  Chelsea  0.4137   
27  2021-08-29                  Burnley             Leeds United  0.3565   
28  2021-08-29        Tottenham Hotspur                  Watford  0.6534   
29  2021-08-29  Wolverhampton Wanderers        Manchester United  0.2141   
30  2021-09-11           Crystal Palace        Tottenham Hotspur  0.2345   
31  2021-09-11           Leicester City          Manchester City  0.1543   
32  2021-09-11                Brentford   Brighton & Hove Albion  0.3332   
33  2021-09-11        Manchester United         Newcastle United  0.7076   
34  2021-09-11                  Watford  Wolverhampton Wanderers  0.3100   
35  2021-09-11              Southampton          West Ham United  0.3282   
36  2021-09-11                  Arsenal             Norwich City  0.5833   
37  2021-09-11                  Chelsea              Aston Villa  0.6941   
38  2021-09-12             Leeds United                Liverpool  0.1796   
39  2021-09-13                  Everton                  Burnley  0.5412   
40  2021-09-17         Newcastle United             Leeds United  0.3663   
41  2021-09-18  Wolverhampton Wanderers                Brentford  0.4942   
42  2021-09-18                  Burnley                  Arsenal  0.3015   
43  2021-09-18             Norwich City                  Watford  0.4123   
44  2021-09-18                Liverpool           Crystal Palace  0.7755   
45  2021-09-18          Manchester City              Southampton  0.8315   
46  2021-09-18              Aston Villa                  Everton  0.3826   
47  2021-09-19          West Ham United        Manchester United  0.2955   
48  2021-09-19   Brighton & Hove Albion           Leicester City  0.4068   
49  2021-09-19        Tottenham Hotspur                  Chelsea  0.2649   
50  2021-09-25        Manchester United              Aston Villa  0.6091   
51  2021-09-25                  Chelsea          Mancheste

In [ ]:
pd.crosstab(season21_22['FTR'], season21_22['B365res'],dropna= True)

B365res      A   H
FTR               
A        0  32  15
D        2  13  27
H        0  11  50

In [ ]:
# create the log of TM ratios 
season21_22['lhTMratio'] = np.log(season21_22['TMhome']/season21_22['TMaway'])

In [ ]:
# create a value = 2 if homewin, 1 if draw, 0 if awaywin
season21_22['winvalue'] = np.where(season21_22['FTR'] == 'H', 2 ,(np.where(season21_22['FTR'] == 'D', 1, 0)))
season21_22

date                Home team                Away team  538hpr  \
0   2021-08-13                Brentford                  Arsenal  0.2240   
1   2021-08-14        Manchester United             Leeds United  0.6282   
2   2021-08-14           Leicester City  Wolverhampton Wanderers  0.5333   
3   2021-08-14                  Everton              Southampton  0.4789   
4   2021-08-14                  Chelsea           Crystal Palace  0.7531   
5   2021-08-14                  Watford              Aston Villa  0.3067   
6   2021-08-14                  Burnley   Brighton & Hove Albion  0.3356   
7   2021-08-14             Norwich City                Liverpool  0.1293   
8   2021-08-15         Newcastle United          West Ham United  0.3533   
9   2021-08-15        Tottenham Hotspur          Manchester City  0.2239   
10  2021-08-21                Liverpool                  Burnley  0.7621   
11  2021-08-21             Leeds United                  Everton  0.4038   
12  2021-08-21          Manchester City             Norwich City  0.8281   
13  2021-08-21           Crystal Palace                Brentford  0.4091   
14  2021-08-21              Aston Villa         Newcastle United  0.4917   
15  2021-08-21   Brighton & Hove Albion                  Watford  0.5466   
16  2021-08-22  Wolverhampton Wanderers        Tottenham Hotspur  0.2905   
17  2021-08-22              Southampton        Manchester United  0.1837   
18  2021-08-22                  Arsenal                  Chelsea  0.2839   
19  2021-08-23          West Ham United           Leicester City  0.3961   
20  2021-08-28          Manchester City                  Arsenal  0.6898   
21  2021-08-28         Newcastle United              Southampton  0.4219   
22  2021-08-28          West Ham United           Crystal Palace  0.5911   
23  2021-08-28             Norwich City           Leicester City  0.2627   
24  2021-08-28              Aston Villa                Brentford  0.5099   
25  2021-08-28   Brighton & Hove Albion                  Everton  0.4250   
26  2021-08-28                Liverpool                  Chelsea  0.4137   
27  2021-08-29                  Burnley             Leeds United  0.3565   
28  2021-08-29        Tottenham Hotspur                  Watford  0.6534   
29  2021-08-29  Wolverhampton Wanderers        Manchester United  0.2141   
30  2021-09-11           Crystal Palace        Tottenham Hotspur  0.2345   
31  2021-09-11           Leicester City          Manchester City  0.1543   
32  2021-09-11                Brentford   Brighton & Hove Albion  0.3332   
33  2021-09-11        Manchester United         Newcastle United  0.7076   
34  2021-09-11                  Watford  Wolverhampton Wanderers  0.3100   
35  2021-09-11              Southampton          West Ham United  0.3282   
36  2021-09-11                  Arsenal             Norwich City  0.5833   
37  2021-09-11                  Chelsea              Aston Villa  0.6941   
38  2021-09-12             Leeds United                Liverpool  0.1796   
39  2021-09-13                  Everton                  Burnley  0.5412   
40  2021-09-17         Newcastle United             Leeds United  0.3663   
41  2021-09-18  Wolverhampton Wanderers                Brentford  0.4942   
42  2021-09-18                  Burnley                  Arsenal  0.3015   
43  2021-09-18             Norwich City                  Watford  0.4123   
44  2021-09-18                Liverpool           Crystal Palace  0.7755   
45  2021-09-18          Manchester City              Southampton  0.8315   
46  2021-09-18              Aston Villa                  Everton  0.3826   
47  2021-09-19          West Ham United        Manchester United  0.2955   
48  2021-09-19   Brighton & Hove Albion           Leicester City  0.4068   
49  2021-09-19        Tottenham Hotspur                  Chelsea  0.2649   
50  2021-09-25        Manchester United              Aston Villa  0.6091   
51  2021-09-25                  Chelsea          Mancheste

In [ ]:
season22 = season21_22[:76]
season22

date                Home team                Away team  538hpr  \
0  2021-08-13                Brentford                  Arsenal  0.2240   
1  2021-08-14        Manchester United             Leeds United  0.6282   
2  2021-08-14           Leicester City  Wolverhampton Wanderers  0.5333   
3  2021-08-14                  Everton              Southampton  0.4789   
4  2021-08-14                  Chelsea           Crystal Palace  0.7531   
5  2021-08-14                  Watford              Aston Villa  0.3067   
6  2021-08-14                  Burnley   Brighton & Hove Albion  0.3356   
7  2021-08-14             Norwich City                Liverpool  0.1293   
8  2021-08-15         Newcastle United          West Ham United  0.3533   
9  2021-08-15        Tottenham Hotspur          Manchester City  0.2239   
10 2021-08-21                Liverpool                  Burnley  0.7621   
11 2021-08-21             Leeds United                  Everton  0.4038   
12 2021-08-21          Manchester City             Norwich City  0.8281   
13 2021-08-21           Crystal Palace                Brentford  0.4091   
14 2021-08-21              Aston Villa         Newcastle United  0.4917   
15 2021-08-21   Brighton & Hove Albion                  Watford  0.5466   
16 2021-08-22  Wolverhampton Wanderers        Tottenham Hotspur  0.2905   
17 2021-08-22              Southampton        Manchester United  0.1837   
18 2021-08-22                  Arsenal                  Chelsea  0.2839   
19 2021-08-23          West Ham United           Leicester City  0.3961   
20 2021-08-28          Manchester City                  Arsenal  0.6898   
21 2021-08-28         Newcastle United              Southampton  0.4219   
22 2021-08-28          West Ham United           Crystal Palace  0.5911   
23 2021-08-28             Norwich City           Leicester City  0.2627   
24 2021-08-28              Aston Villa                Brentford  0.5099   
25 2021-08-28   Brighton & Hove Albion                  Everton  0.4250   
26 2021-08-28                Liverpool                  Chelsea  0.4137   
27 2021-08-29                  Burnley             Leeds United  0.3565   
28 2021-08-29        Tottenham Hotspur                  Watford  0.6534   
29 2021-08-29  Wolverhampton Wanderers        Manchester United  0.2141   
30 2021-09-11           Crystal Palace        Tottenham Hotspur  0.2345   
31 2021-09-11           Leicester City          Manchester City  0.1543   
32 2021-09-11                Brentford   Brighton & Hove Albion  0.3332   
33 2021-09-11        Manchester United         Newcastle United  0.7076   
34 2021-09-11                  Watford  Wolverhampton Wanderers  0.3100   
35 2021-09-11              Southampton          West Ham United  0.3282   
36 2021-09-11                  Arsenal             Norwich City  0.5833   
37 2021-09-11                  Chelsea              Aston Villa  0.6941   
38 2021-09-12             Leeds United                Liverpool  0.1796   
39 2021-09-13                  Everton                  Burnley  0.5412   
40 2021-09-17         Newcastle United             Leeds United  0.3663   
41 2021-09-18  Wolverhampton Wanderers                Brentford  0.4942   
42 2021-09-18                  Burnley                  Arsenal  0.3015   
43 2021-09-18             Norwich City                  Watford  0.4123   
44 2021-09-18                Liverpool           Crystal Palace  0.7755   
45 2021-09-18          Manchester City              Southampton  0.8315   
46 2021-09-18              Aston Villa                  Everton  0.3826   
47 2021-09-19          West Ham United        Manchester United  0.2955   
48 2021-09-19   Brighton & Hove Albion           Leicester City  0.4068   
49 2021-09-19        Tottenham Hotspur                  Chelsea  0.2649   
50 2021-09-25        Manchester United              Aston Villa  0.6091   
51 2021-09-25                  Chelsea          Manchester City  0.3239   
52 2021-09-25                  Wat

In [ ]:
season22.dropna(inplace=True)
season22.shape

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



(76, 21)

In [ ]:
ol2 = OrderedModel(season22.winvalue, season22.lhTMratio, distr='logit')

In [ ]:
res_log2 = ol2.fit(method='bfgs', disp=False)
res_log2.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                             OrderedModel Results                             
==============================================================================
Dep. Variable:               winvalue   Log-Likelihood:                -71.950
Model:                   OrderedModel   AIC:                             149.9
Method:            Maximum Likelihood   BIC:                             156.9
Date:                Tue, 14 Dec 2021                                         
Time:                        08:44:25                                         
No. Observations:                  76                                         
Df Residuals:                      73                                         
Df Model:                           3                                         
==============================================================================
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
lhTMratio      1.2580      0.304      4.141      0.000       0.663       1.853
0/1           -0.9533      0.275     -3.467      0.001      -1.492      -0.414
1/2            0.3582      0.198      1.806      0.071      -0.031       0.747
==============================================================================
"""

In [ ]:
#%% To get the coefficients and the intercepts
print(f'beta = {res_log2.params[0]:.4f}')
print(f'interceptAD = {res_log2.params[1]:.4f}')
print(f'interceptDH = {res_log2.params[2]:.4f}')

beta = 1.2580
interceptAD = -0.9533
interceptDH = 0.3582


In [ ]:
# Predicted probabilities

season21_22['predA'] = 1/(1+np.exp(-(res_log2.params[1]-res_log2.params[0]*season21_22['lhTMratio'])))
season21_22['predD'] = 1/(1+np.exp(-(res_log2.params[2]-res_log2.params[0]*season21_22['lhTMratio']))) - season21_22['predA']
season21_22['predH'] = 1 - season21_22['predA'] - season21_22['predD']

pd.set_option('display.max_columns', 50)
season21_22

date                Home team                Away team  538hpr  \
0   2021-08-13                Brentford                  Arsenal  0.2240   
1   2021-08-14        Manchester United             Leeds United  0.6282   
2   2021-08-14           Leicester City  Wolverhampton Wanderers  0.5333   
3   2021-08-14                  Everton              Southampton  0.4789   
4   2021-08-14                  Chelsea           Crystal Palace  0.7531   
5   2021-08-14                  Watford              Aston Villa  0.3067   
6   2021-08-14                  Burnley   Brighton & Hove Albion  0.3356   
7   2021-08-14             Norwich City                Liverpool  0.1293   
8   2021-08-15         Newcastle United          West Ham United  0.3533   
9   2021-08-15        Tottenham Hotspur          Manchester City  0.2239   
10  2021-08-21                Liverpool                  Burnley  0.7621   
11  2021-08-21             Leeds United                  Everton  0.4038   
12  2021-08-21          Manchester City             Norwich City  0.8281   
13  2021-08-21           Crystal Palace                Brentford  0.4091   
14  2021-08-21              Aston Villa         Newcastle United  0.4917   
15  2021-08-21   Brighton & Hove Albion                  Watford  0.5466   
16  2021-08-22  Wolverhampton Wanderers        Tottenham Hotspur  0.2905   
17  2021-08-22              Southampton        Manchester United  0.1837   
18  2021-08-22                  Arsenal                  Chelsea  0.2839   
19  2021-08-23          West Ham United           Leicester City  0.3961   
20  2021-08-28          Manchester City                  Arsenal  0.6898   
21  2021-08-28         Newcastle United              Southampton  0.4219   
22  2021-08-28          West Ham United           Crystal Palace  0.5911   
23  2021-08-28             Norwich City           Leicester City  0.2627   
24  2021-08-28              Aston Villa                Brentford  0.5099   
25  2021-08-28   Brighton & Hove Albion                  Everton  0.4250   
26  2021-08-28                Liverpool                  Chelsea  0.4137   
27  2021-08-29                  Burnley             Leeds United  0.3565   
28  2021-08-29        Tottenham Hotspur                  Watford  0.6534   
29  2021-08-29  Wolverhampton Wanderers        Manchester United  0.2141   
30  2021-09-11           Crystal Palace        Tottenham Hotspur  0.2345   
31  2021-09-11           Leicester City          Manchester City  0.1543   
32  2021-09-11                Brentford   Brighton & Hove Albion  0.3332   
33  2021-09-11        Manchester United         Newcastle United  0.7076   
34  2021-09-11                  Watford  Wolverhampton Wanderers  0.3100   
35  2021-09-11              Southampton          West Ham United  0.3282   
36  2021-09-11                  Arsenal             Norwich City  0.5833   
37  2021-09-11                  Chelsea              Aston Villa  0.6941   
38  2021-09-12             Leeds United                Liverpool  0.1796   
39  2021-09-13                  Everton                  Burnley  0.5412   
40  2021-09-17         Newcastle United             Leeds United  0.3663   
41  2021-09-18  Wolverhampton Wanderers                Brentford  0.4942   
42  2021-09-18                  Burnley                  Arsenal  0.3015   
43  2021-09-18             Norwich City                  Watford  0.4123   
44  2021-09-18                Liverpool           Crystal Palace  0.7755   
45  2021-09-18          Manchester City              Southampton  0.8315   
46  2021-09-18              Aston Villa                  Everton  0.3826   
47  2021-09-19          West Ham United        Manchester United  0.2955   
48  2021-09-19   Brighton & Hove Albion           Leicester City  0.4068   
49  2021-09-19        Tottenham Hotspur                  Chelsea  0.2649   
50  2021-09-25        Manchester United              Aston Villa  0.6091   
51  2021-09-25                  Chelsea          Mancheste

In [ ]:
# Result prediction

season21_22['Maxprob'] =season21_22[['predA','predD','predH']].max(axis=1)
season21_22['logitpred']=np.where(season21_22['Maxprob']==season21_22['predA'],'A',\
                               np.where(season21_22['Maxprob']==season21_22['predD'],'D','H'))
season21_22['logittrue']= np.where(season21_22['logitpred'] == season21_22['FTR'],1,0)
season21_22

date                Home team                Away team  538hpr  \
0   2021-08-13                Brentford                  Arsenal  0.2240   
1   2021-08-14        Manchester United             Leeds United  0.6282   
2   2021-08-14           Leicester City  Wolverhampton Wanderers  0.5333   
3   2021-08-14                  Everton              Southampton  0.4789   
4   2021-08-14                  Chelsea           Crystal Palace  0.7531   
5   2021-08-14                  Watford              Aston Villa  0.3067   
6   2021-08-14                  Burnley   Brighton & Hove Albion  0.3356   
7   2021-08-14             Norwich City                Liverpool  0.1293   
8   2021-08-15         Newcastle United          West Ham United  0.3533   
9   2021-08-15        Tottenham Hotspur          Manchester City  0.2239   
10  2021-08-21                Liverpool                  Burnley  0.7621   
11  2021-08-21             Leeds United                  Everton  0.4038   
12  2021-08-21          Manchester City             Norwich City  0.8281   
13  2021-08-21           Crystal Palace                Brentford  0.4091   
14  2021-08-21              Aston Villa         Newcastle United  0.4917   
15  2021-08-21   Brighton & Hove Albion                  Watford  0.5466   
16  2021-08-22  Wolverhampton Wanderers        Tottenham Hotspur  0.2905   
17  2021-08-22              Southampton        Manchester United  0.1837   
18  2021-08-22                  Arsenal                  Chelsea  0.2839   
19  2021-08-23          West Ham United           Leicester City  0.3961   
20  2021-08-28          Manchester City                  Arsenal  0.6898   
21  2021-08-28         Newcastle United              Southampton  0.4219   
22  2021-08-28          West Ham United           Crystal Palace  0.5911   
23  2021-08-28             Norwich City           Leicester City  0.2627   
24  2021-08-28              Aston Villa                Brentford  0.5099   
25  2021-08-28   Brighton & Hove Albion                  Everton  0.4250   
26  2021-08-28                Liverpool                  Chelsea  0.4137   
27  2021-08-29                  Burnley             Leeds United  0.3565   
28  2021-08-29        Tottenham Hotspur                  Watford  0.6534   
29  2021-08-29  Wolverhampton Wanderers        Manchester United  0.2141   
30  2021-09-11           Crystal Palace        Tottenham Hotspur  0.2345   
31  2021-09-11           Leicester City          Manchester City  0.1543   
32  2021-09-11                Brentford   Brighton & Hove Albion  0.3332   
33  2021-09-11        Manchester United         Newcastle United  0.7076   
34  2021-09-11                  Watford  Wolverhampton Wanderers  0.3100   
35  2021-09-11              Southampton          West Ham United  0.3282   
36  2021-09-11                  Arsenal             Norwich City  0.5833   
37  2021-09-11                  Chelsea              Aston Villa  0.6941   
38  2021-09-12             Leeds United                Liverpool  0.1796   
39  2021-09-13                  Everton                  Burnley  0.5412   
40  2021-09-17         Newcastle United             Leeds United  0.3663   
41  2021-09-18  Wolverhampton Wanderers                Brentford  0.4942   
42  2021-09-18                  Burnley                  Arsenal  0.3015   
43  2021-09-18             Norwich City                  Watford  0.4123   
44  2021-09-18                Liverpool           Crystal Palace  0.7755   
45  2021-09-18          Manchester City              Southampton  0.8315   
46  2021-09-18              Aston Villa                  Everton  0.3826   
47  2021-09-19          West Ham United        Manchester United  0.2955   
48  2021-09-19   Brighton & Hove Albion           Leicester City  0.4068   
49  2021-09-19        Tottenham Hotspur                  Chelsea  0.2649   
50  2021-09-25        Manchester United              Aston Villa  0.6091   
51  2021-09-25                  Chelsea          Mancheste

In [ ]:
trunc21_22 = season21_22[76:150].copy()
trunc21_22.describe()

538hpr     538apr     538dpr       FTHG       FTAG      month  \
count  74.000000  74.000000  74.000000  73.000000  73.000000  74.000000   
mean    0.412959   0.350696   0.236339   1.520548   1.383562  10.932432   
std     0.176984   0.171675   0.040442   1.292173   1.265242   0.746335   
min     0.082500   0.043000   0.116100   0.000000   0.000000  10.000000   
25%     0.308025   0.243200   0.220625   1.000000   0.000000  10.000000   
50%     0.401500   0.333150   0.252150   1.000000   1.000000  11.000000   
75%     0.492550   0.437975   0.262600   2.000000   2.000000  11.000000   
max     0.840800   0.769500   0.289500   7.000000   5.000000  12.000000   

             day    year  notplayed      TMhome      TMaway      B365H  \
count  74.000000    74.0  74.000000   74.000000   74.000000  73.000000   
mean   16.608108  2021.0   0.013514  398.547027  418.573784   3.077808   
std    10.748453     0.0   0.116248  244.073679  260.857741   2.273688   
min     1.000000  2021.0   0.000000  130.770000  130.770000   1.140000   
25%     5.250000  2021.0   0.000000  221.772500  224.510000   1.650000   
50%    20.000000  2021.0   0.000000  332.260000  332.260000   2.370000   
75%    27.000000  2021.0   0.000000  507.150000  627.530000   3.200000   
max    31.000000  2021.0   1.000000  970.020000  970.020000  12.000000   

           B365D      B365A  lhTMratio   winvalue      predA      predD  \
count  73.000000  73.000000  74.000000  74.000000  74.000000  74.000000   
mean    4.124384   4.349315  -0.032948   1.094595   0.326019   0.253079   
std     1.122355   3.711177   0.888901   0.846733   0.205369   0.066913   
min     3.200000   1.200000  -2.002501   0.000000   0.037853   0.089576   
25%     3.400000   2.200000  -0.648568   0.000000   0.168151   0.194888   
50%     3.600000   3.000000  -0.014255   1.000000   0.281834   0.286122   
75%     4.750000   5.250000   0.513231   2.000000   0.465732   0.308594   
max     8.000000  19.000000   1.814105   2.000000   0.827183   0.316519   

           predH    Maxprob  logittrue  
count  74.000000  74.000000  74.000000  
mean    0.420902   0.554429   0.459459  
std     0.226524   0.154103   0.501756  
min     0.053283   0.350554   0.000000  
25%     0.236291   0.421355   0.000000  
50%     0.407051   0.504920   0.000000  
75%     0.571349   0.702872   1.000000  
max     0.872571   0.872571   1.000000

In [ ]:
# Model success rate
trunc21_22['logittrue'].mean()

0.4594594594594595

In [ ]:
trunc21_22['B365true']= np.where(trunc21_22['B365res'] == trunc21_22['FTR'],1,0)
trunc21_22

date                Home team                Away team  538hpr  \
76  2021-10-16                Brentford                  Chelsea  0.1773   
77  2021-10-17                  Everton          West Ham United  0.4066   
78  2021-10-17         Newcastle United        Tottenham Hotspur  0.3035   
79  2021-10-18                  Arsenal           Crystal Palace  0.5285   
80  2021-10-22                  Arsenal              Aston Villa  0.4613   
81  2021-10-23                  Chelsea             Norwich City  0.7703   
82  2021-10-23              Southampton                  Burnley  0.4535   
83  2021-10-23           Crystal Palace         Newcastle United  0.4461   
84  2021-10-23                  Everton                  Watford  0.5675   
85  2021-10-23             Leeds United  Wolverhampton Wanderers  0.3900   
86  2021-10-23   Brighton & Hove Albion          Manchester City  0.1188   
87  2021-10-24                Brentford           Leicester City  0.3590   
88  2021-10-24          West Ham United        Tottenham Hotspur  0.4407   
89  2021-10-24        Manchester United                Liverpool  0.2892   
90  2021-10-30           Leicester City                  Arsenal  0.3964   
91  2021-10-30         Newcastle United                  Chelsea  0.1470   
92  2021-10-30                  Watford              Southampton  0.3453   
93  2021-10-30                  Burnley                Brentford  0.3793   
94  2021-10-30          Manchester City           Crystal Palace  0.8408   
95  2021-10-30                Liverpool   Brighton & Hove Albion  0.7415   
96  2021-10-30        Tottenham Hotspur        Manchester United  0.3216   
97  2021-10-31             Norwich City             Leeds United  0.2705   
98  2021-10-31              Aston Villa          West Ham United  0.3494   
99  2021-11-01  Wolverhampton Wanderers                  Everton  0.4377   
100 2021-11-05              Southampton              Aston Villa  0.4098   
101 2021-11-06        Manchester United          Manchester City  0.2246   
102 2021-11-06           Crystal Palace  Wolverhampton Wanderers  0.3840   
103 2021-11-06                  Chelsea                  Burnley  0.7420   
104 2021-11-06                Brentford             Norwich City  0.5631   
105 2021-11-06   Brighton & Hove Albion         Newcastle United  0.5580   
106 2021-11-07                  Everton        Tottenham Hotspur  0.3861   
107 2021-11-07                  Arsenal                  Watford  0.6195   
108 2021-11-07             Leeds United           Leicester City  0.3776   
109 2021-11-07          West Ham United                Liverpool  0.2192   
110 2021-11-20           Leicester City                  Chelsea  0.2046   
111 2021-11-20                  Burnley           Crystal Palace  0.3898   
112 2021-11-20                  Watford        Manchester United  0.1957   
113 2021-11-20             Norwich City              Southampton  0.2865   
114 2021-11-20              Aston Villa   Brighton & Hove Albion  0.3729   
115 2021-11-20  Wolverhampton Wanderers          West Ham United  0.2841   
116 2021-11-20         Newcastle United                Brentford  0.3583   
117 2021-11-20                Liverpool                  Arsenal  0.6733   
118 2021-11-21          Manchester City                  Everton  0.8212   
119 2021-11-21        Tottenham Hotspur             Leeds United  0.4472   
120 2021-11-27                  Arsenal         Newcastle United  0.5674   
121 2021-11-27             Norwich City  Wolverhampton Wanderers  0.2762   
122 2021-11-27           Crystal Palace              Aston Villa  0.4161   
123 2021-11-27                Liverpool              Southampton  0.7952   
124 2021-11-27   Brighton & Hove Albion             Leeds United  0.4487   
125 2021-11-28                Brentford                  Everton  0.4070   
126 2021-11-28                  Burnley        Tottenham Hotspur  0.3471   
127 2021-11-28          Manchester City          West Ham 

In [ ]:
trunc21_22['B365true'].mean()

0.5405405405405406

In [ ]:
# Outcome value for calculating Brier Score

trunc21_22['Houtcome']= np.where(trunc21_22['FTR']=='H',1,0)
trunc21_22['Doutcome']= np.where(trunc21_22['FTR']=='D',1,0)
trunc21_22['Aoutcome']= np.where(trunc21_22['FTR']=='A',1,0)
trunc21_22

date                Home team                Away team  538hpr  \
76  2021-10-16                Brentford                  Chelsea  0.1773   
77  2021-10-17                  Everton          West Ham United  0.4066   
78  2021-10-17         Newcastle United        Tottenham Hotspur  0.3035   
79  2021-10-18                  Arsenal           Crystal Palace  0.5285   
80  2021-10-22                  Arsenal              Aston Villa  0.4613   
81  2021-10-23                  Chelsea             Norwich City  0.7703   
82  2021-10-23              Southampton                  Burnley  0.4535   
83  2021-10-23           Crystal Palace         Newcastle United  0.4461   
84  2021-10-23                  Everton                  Watford  0.5675   
85  2021-10-23             Leeds United  Wolverhampton Wanderers  0.3900   
86  2021-10-23   Brighton & Hove Albion          Manchester City  0.1188   
87  2021-10-24                Brentford           Leicester City  0.3590   
88  2021-10-24          West Ham United        Tottenham Hotspur  0.4407   
89  2021-10-24        Manchester United                Liverpool  0.2892   
90  2021-10-30           Leicester City                  Arsenal  0.3964   
91  2021-10-30         Newcastle United                  Chelsea  0.1470   
92  2021-10-30                  Watford              Southampton  0.3453   
93  2021-10-30                  Burnley                Brentford  0.3793   
94  2021-10-30          Manchester City           Crystal Palace  0.8408   
95  2021-10-30                Liverpool   Brighton & Hove Albion  0.7415   
96  2021-10-30        Tottenham Hotspur        Manchester United  0.3216   
97  2021-10-31             Norwich City             Leeds United  0.2705   
98  2021-10-31              Aston Villa          West Ham United  0.3494   
99  2021-11-01  Wolverhampton Wanderers                  Everton  0.4377   
100 2021-11-05              Southampton              Aston Villa  0.4098   
101 2021-11-06        Manchester United          Manchester City  0.2246   
102 2021-11-06           Crystal Palace  Wolverhampton Wanderers  0.3840   
103 2021-11-06                  Chelsea                  Burnley  0.7420   
104 2021-11-06                Brentford             Norwich City  0.5631   
105 2021-11-06   Brighton & Hove Albion         Newcastle United  0.5580   
106 2021-11-07                  Everton        Tottenham Hotspur  0.3861   
107 2021-11-07                  Arsenal                  Watford  0.6195   
108 2021-11-07             Leeds United           Leicester City  0.3776   
109 2021-11-07          West Ham United                Liverpool  0.2192   
110 2021-11-20           Leicester City                  Chelsea  0.2046   
111 2021-11-20                  Burnley           Crystal Palace  0.3898   
112 2021-11-20                  Watford        Manchester United  0.1957   
113 2021-11-20             Norwich City              Southampton  0.2865   
114 2021-11-20              Aston Villa   Brighton & Hove Albion  0.3729   
115 2021-11-20  Wolverhampton Wanderers          West Ham United  0.2841   
116 2021-11-20         Newcastle United                Brentford  0.3583   
117 2021-11-20                Liverpool                  Arsenal  0.6733   
118 2021-11-21          Manchester City                  Everton  0.8212   
119 2021-11-21        Tottenham Hotspur             Leeds United  0.4472   
120 2021-11-27                  Arsenal         Newcastle United  0.5674   
121 2021-11-27             Norwich City  Wolverhampton Wanderers  0.2762   
122 2021-11-27           Crystal Palace              Aston Villa  0.4161   
123 2021-11-27                Liverpool              Southampton  0.7952   
124 2021-11-27   Brighton & Hove Albion             Leeds United  0.4487   
125 2021-11-28                Brentford                  Everton  0.4070   
126 2021-11-28                  Burnley        Tottenham Hotspur  0.3471   
127 2021-11-28          Manchester City          West Ham 

In [ ]:
trunc21_22['B365HPr']= 1/(trunc21_22['B365H'])/(1/(trunc21_22['B365H'])+ 1/(trunc21_22['B365D'])+ 1/(trunc21_22['B365A']))
trunc21_22['B365DPr']= 1/(trunc21_22['B365D'])/(1/(trunc21_22['B365H'])+ 1/(trunc21_22['B365D'])+ 1/(trunc21_22['B365A']))
trunc21_22['B365APr']= 1/(trunc21_22['B365A'])/(1/(trunc21_22['B365H'])+ 1/(trunc21_22['B365D'])+ 1/(trunc21_22['B365A']))
trunc21_22

date                Home team                Away team  538hpr  \
76  2021-10-16                Brentford                  Chelsea  0.1773   
77  2021-10-17                  Everton          West Ham United  0.4066   
78  2021-10-17         Newcastle United        Tottenham Hotspur  0.3035   
79  2021-10-18                  Arsenal           Crystal Palace  0.5285   
80  2021-10-22                  Arsenal              Aston Villa  0.4613   
81  2021-10-23                  Chelsea             Norwich City  0.7703   
82  2021-10-23              Southampton                  Burnley  0.4535   
83  2021-10-23           Crystal Palace         Newcastle United  0.4461   
84  2021-10-23                  Everton                  Watford  0.5675   
85  2021-10-23             Leeds United  Wolverhampton Wanderers  0.3900   
86  2021-10-23   Brighton & Hove Albion          Manchester City  0.1188   
87  2021-10-24                Brentford           Leicester City  0.3590   
88  2021-10-24          West Ham United        Tottenham Hotspur  0.4407   
89  2021-10-24        Manchester United                Liverpool  0.2892   
90  2021-10-30           Leicester City                  Arsenal  0.3964   
91  2021-10-30         Newcastle United                  Chelsea  0.1470   
92  2021-10-30                  Watford              Southampton  0.3453   
93  2021-10-30                  Burnley                Brentford  0.3793   
94  2021-10-30          Manchester City           Crystal Palace  0.8408   
95  2021-10-30                Liverpool   Brighton & Hove Albion  0.7415   
96  2021-10-30        Tottenham Hotspur        Manchester United  0.3216   
97  2021-10-31             Norwich City             Leeds United  0.2705   
98  2021-10-31              Aston Villa          West Ham United  0.3494   
99  2021-11-01  Wolverhampton Wanderers                  Everton  0.4377   
100 2021-11-05              Southampton              Aston Villa  0.4098   
101 2021-11-06        Manchester United          Manchester City  0.2246   
102 2021-11-06           Crystal Palace  Wolverhampton Wanderers  0.3840   
103 2021-11-06                  Chelsea                  Burnley  0.7420   
104 2021-11-06                Brentford             Norwich City  0.5631   
105 2021-11-06   Brighton & Hove Albion         Newcastle United  0.5580   
106 2021-11-07                  Everton        Tottenham Hotspur  0.3861   
107 2021-11-07                  Arsenal                  Watford  0.6195   
108 2021-11-07             Leeds United           Leicester City  0.3776   
109 2021-11-07          West Ham United                Liverpool  0.2192   
110 2021-11-20           Leicester City                  Chelsea  0.2046   
111 2021-11-20                  Burnley           Crystal Palace  0.3898   
112 2021-11-20                  Watford        Manchester United  0.1957   
113 2021-11-20             Norwich City              Southampton  0.2865   
114 2021-11-20              Aston Villa   Brighton & Hove Albion  0.3729   
115 2021-11-20  Wolverhampton Wanderers          West Ham United  0.2841   
116 2021-11-20         Newcastle United                Brentford  0.3583   
117 2021-11-20                Liverpool                  Arsenal  0.6733   
118 2021-11-21          Manchester City                  Everton  0.8212   
119 2021-11-21        Tottenham Hotspur             Leeds United  0.4472   
120 2021-11-27                  Arsenal         Newcastle United  0.5674   
121 2021-11-27             Norwich City  Wolverhampton Wanderers  0.2762   
122 2021-11-27           Crystal Palace              Aston Villa  0.4161   
123 2021-11-27                Liverpool              Southampton  0.7952   
124 2021-11-27   Brighton & Hove Albion             Leeds United  0.4487   
125 2021-11-28                Brentford                  Everton  0.4070   
126 2021-11-28                  Burnley        Tottenham Hotspur  0.3471   
127 2021-11-28          Manchester City          West Ham 

In [ ]:
# Model Brier score

Brierlogit = ((trunc21_22['predH'] - trunc21_22['Houtcome'])**2 +(trunc21_22['predD'] - trunc21_22['Doutcome'])**2 +\
             (trunc21_22['predA'] - trunc21_22['Aoutcome'])**2).sum()/74
Brierlogit

0.6113120267678518

In [ ]:
# Bookie Brier score (lower is better)

BrierB365 = ((trunc21_22['B365HPr'] - trunc21_22['Houtcome'])**2 +(trunc21_22['B365DPr'] - trunc21_22['Doutcome'])**2 +\
             (trunc21_22['B365APr'] - trunc21_22['Aoutcome'])**2).sum()/74
BrierB365

0.5709530329767158

In [ ]:
pd.crosstab(trunc21_22['FTR'], trunc21_22['B365res'],dropna= True)

B365res      A   H
FTR               
A        0  16   7
D        2   3  16
H        0   6  24

In [ ]:
pd.crosstab(trunc21_22['FTR'], trunc21_22['logitpred'],dropna= True)

logitpred   A   H
FTR              
A          15   8
D           7  14
H          11  19

In [ ]:
# Most likely outcome

trunc21_22['538res']= np.where((trunc21_22['538hpr']>trunc21_22['538dpr']) & (trunc21_22['538hpr']>trunc21_22['538apr']),'H',\
                            np.where((trunc21_22['538dpr']>trunc21_22['538hpr']) & (trunc21_22['538dpr']>trunc21_22['538apr']),'D',\
                                    np.where((trunc21_22['538apr']>trunc21_22['538hpr']) & (trunc21_22['538apr']>trunc21_22['538dpr']),'A',"")))
trunc21_22

date                Home team                Away team  538hpr  \
76  2021-10-16                Brentford                  Chelsea  0.1773   
77  2021-10-17                  Everton          West Ham United  0.4066   
78  2021-10-17         Newcastle United        Tottenham Hotspur  0.3035   
79  2021-10-18                  Arsenal           Crystal Palace  0.5285   
80  2021-10-22                  Arsenal              Aston Villa  0.4613   
81  2021-10-23                  Chelsea             Norwich City  0.7703   
82  2021-10-23              Southampton                  Burnley  0.4535   
83  2021-10-23           Crystal Palace         Newcastle United  0.4461   
84  2021-10-23                  Everton                  Watford  0.5675   
85  2021-10-23             Leeds United  Wolverhampton Wanderers  0.3900   
86  2021-10-23   Brighton & Hove Albion          Manchester City  0.1188   
87  2021-10-24                Brentford           Leicester City  0.3590   
88  2021-10-24          West Ham United        Tottenham Hotspur  0.4407   
89  2021-10-24        Manchester United                Liverpool  0.2892   
90  2021-10-30           Leicester City                  Arsenal  0.3964   
91  2021-10-30         Newcastle United                  Chelsea  0.1470   
92  2021-10-30                  Watford              Southampton  0.3453   
93  2021-10-30                  Burnley                Brentford  0.3793   
94  2021-10-30          Manchester City           Crystal Palace  0.8408   
95  2021-10-30                Liverpool   Brighton & Hove Albion  0.7415   
96  2021-10-30        Tottenham Hotspur        Manchester United  0.3216   
97  2021-10-31             Norwich City             Leeds United  0.2705   
98  2021-10-31              Aston Villa          West Ham United  0.3494   
99  2021-11-01  Wolverhampton Wanderers                  Everton  0.4377   
100 2021-11-05              Southampton              Aston Villa  0.4098   
101 2021-11-06        Manchester United          Manchester City  0.2246   
102 2021-11-06           Crystal Palace  Wolverhampton Wanderers  0.3840   
103 2021-11-06                  Chelsea                  Burnley  0.7420   
104 2021-11-06                Brentford             Norwich City  0.5631   
105 2021-11-06   Brighton & Hove Albion         Newcastle United  0.5580   
106 2021-11-07                  Everton        Tottenham Hotspur  0.3861   
107 2021-11-07                  Arsenal                  Watford  0.6195   
108 2021-11-07             Leeds United           Leicester City  0.3776   
109 2021-11-07          West Ham United                Liverpool  0.2192   
110 2021-11-20           Leicester City                  Chelsea  0.2046   
111 2021-11-20                  Burnley           Crystal Palace  0.3898   
112 2021-11-20                  Watford        Manchester United  0.1957   
113 2021-11-20             Norwich City              Southampton  0.2865   
114 2021-11-20              Aston Villa   Brighton & Hove Albion  0.3729   
115 2021-11-20  Wolverhampton Wanderers          West Ham United  0.2841   
116 2021-11-20         Newcastle United                Brentford  0.3583   
117 2021-11-20                Liverpool                  Arsenal  0.6733   
118 2021-11-21          Manchester City                  Everton  0.8212   
119 2021-11-21        Tottenham Hotspur             Leeds United  0.4472   
120 2021-11-27                  Arsenal         Newcastle United  0.5674   
121 2021-11-27             Norwich City  Wolverhampton Wanderers  0.2762   
122 2021-11-27           Crystal Palace              Aston Villa  0.4161   
123 2021-11-27                Liverpool              Southampton  0.7952   
124 2021-11-27   Brighton & Hove Albion             Leeds United  0.4487   
125 2021-11-28                Brentford                  Everton  0.4070   
126 2021-11-28                  Burnley        Tottenham Hotspur  0.3471   
127 2021-11-28          Manchester City          West Ham 

In [ ]:
# now identify the forecast successes of FiveThirtyEight

trunc21_22['538true']= np.where(trunc21_22['538res'] == trunc21_22['FTR'],1,0)
trunc21_22

date                Home team                Away team  538hpr  \
76  2021-10-16                Brentford                  Chelsea  0.1773   
77  2021-10-17                  Everton          West Ham United  0.4066   
78  2021-10-17         Newcastle United        Tottenham Hotspur  0.3035   
79  2021-10-18                  Arsenal           Crystal Palace  0.5285   
80  2021-10-22                  Arsenal              Aston Villa  0.4613   
81  2021-10-23                  Chelsea             Norwich City  0.7703   
82  2021-10-23              Southampton                  Burnley  0.4535   
83  2021-10-23           Crystal Palace         Newcastle United  0.4461   
84  2021-10-23                  Everton                  Watford  0.5675   
85  2021-10-23             Leeds United  Wolverhampton Wanderers  0.3900   
86  2021-10-23   Brighton & Hove Albion          Manchester City  0.1188   
87  2021-10-24                Brentford           Leicester City  0.3590   
88  2021-10-24          West Ham United        Tottenham Hotspur  0.4407   
89  2021-10-24        Manchester United                Liverpool  0.2892   
90  2021-10-30           Leicester City                  Arsenal  0.3964   
91  2021-10-30         Newcastle United                  Chelsea  0.1470   
92  2021-10-30                  Watford              Southampton  0.3453   
93  2021-10-30                  Burnley                Brentford  0.3793   
94  2021-10-30          Manchester City           Crystal Palace  0.8408   
95  2021-10-30                Liverpool   Brighton & Hove Albion  0.7415   
96  2021-10-30        Tottenham Hotspur        Manchester United  0.3216   
97  2021-10-31             Norwich City             Leeds United  0.2705   
98  2021-10-31              Aston Villa          West Ham United  0.3494   
99  2021-11-01  Wolverhampton Wanderers                  Everton  0.4377   
100 2021-11-05              Southampton              Aston Villa  0.4098   
101 2021-11-06        Manchester United          Manchester City  0.2246   
102 2021-11-06           Crystal Palace  Wolverhampton Wanderers  0.3840   
103 2021-11-06                  Chelsea                  Burnley  0.7420   
104 2021-11-06                Brentford             Norwich City  0.5631   
105 2021-11-06   Brighton & Hove Albion         Newcastle United  0.5580   
106 2021-11-07                  Everton        Tottenham Hotspur  0.3861   
107 2021-11-07                  Arsenal                  Watford  0.6195   
108 2021-11-07             Leeds United           Leicester City  0.3776   
109 2021-11-07          West Ham United                Liverpool  0.2192   
110 2021-11-20           Leicester City                  Chelsea  0.2046   
111 2021-11-20                  Burnley           Crystal Palace  0.3898   
112 2021-11-20                  Watford        Manchester United  0.1957   
113 2021-11-20             Norwich City              Southampton  0.2865   
114 2021-11-20              Aston Villa   Brighton & Hove Albion  0.3729   
115 2021-11-20  Wolverhampton Wanderers          West Ham United  0.2841   
116 2021-11-20         Newcastle United                Brentford  0.3583   
117 2021-11-20                Liverpool                  Arsenal  0.6733   
118 2021-11-21          Manchester City                  Everton  0.8212   
119 2021-11-21        Tottenham Hotspur             Leeds United  0.4472   
120 2021-11-27                  Arsenal         Newcastle United  0.5674   
121 2021-11-27             Norwich City  Wolverhampton Wanderers  0.2762   
122 2021-11-27           Crystal Palace              Aston Villa  0.4161   
123 2021-11-27                Liverpool              Southampton  0.7952   
124 2021-11-27   Brighton & Hove Albion             Leeds United  0.4487   
125 2021-11-28                Brentford                  Everton  0.4070   
126 2021-11-28                  Burnley        Tottenham Hotspur  0.3471   
127 2021-11-28          Manchester City          West Ham 

In [ ]:
# 538 model success rate

trunc21_22['538true'].mean()

0.5405405405405406

In [ ]:
# 538 Brier score (lower is better)

Brier538 = ((trunc21_22['538hpr'] - trunc21_22['Houtcome'])**2 +(trunc21_22['538dpr'] - trunc21_22['Doutcome'])**2 +\
             (trunc21_22['538apr'] - trunc21_22['Aoutcome'])**2).sum()/74
Brier538

0.5882615435135136

In [ ]:
pd.crosstab(trunc21_22['FTR'], trunc21_22['538res'],margins = True,dropna= True)

538res   A   H  All
FTR                
A       17   6   23
D        4  17   21
H        7  23   30
All     28  46   74

In [ ]:
pd.crosstab(trunc21_22['FTR'], trunc21_22['B365res'],margins = True,dropna= True)

B365res      A   H  All
FTR                    
A        0  16   7   23
D        2   3  16   21
H        0   6  24   30
All      2  25  47   74

In [ ]:
pd.crosstab(trunc21_22['FTR'], trunc21_22['logitpred'],margins = True,dropna= True)

logitpred   A   H  All
FTR                   
A          15   8   23
D           7  14   21
H          11  19   30
All        33  41   74

In [ ]:
# Percentage of highest probability forecasts that were the same for the bookmaker and our model

same_B365_logit = np.where(trunc21_22['B365res'] == trunc21_22['logitpred'],1,0).sum()/74
same_B365_logit

0.7837837837837838

In [ ]:
# Percentage of highest probability forecasts that were the same for the bookmaker and the FiveThirtyEight model

same_B365_538 = np.where(trunc21_22['B365res'] == trunc21_22['538res'],1,0).sum()/74
same_B365_538

0.8918918918918919

In [ ]:
season21_22.to_excel("forecasts21_22.xlsx")

In [ ]:
# load the Premier League table at the date of the suspension

Table = pd.read_excel("Premier League table Dec 12 2021.xlsx")
Table

Position                     club  Played  Won   Drawn  Lost   F   A  \
0          1          Manchester City      16    12      2     2  33   9   
1          2                Liverpool      16    11      4     1  45  12   
2          3                  Chelsea      16    11      3     2  38  11   
3          4          West Ham United      15     8      3     4  28  19   
4          5        Manchester United      16     8      3     5  26  24   
5          6                  Arsenal      16     8      2     6  21  22   
6          7        Tottenham Hotspur      14     8      1     5  16  17   
7          8  Wolverhampton Wanderers      16     6      3     7  12  14   
8          9                Brentford      16     5      5     6  21  22   
9         10   Brighton & Hove Albion      15     4      8     3  14  16   
10        11           Leicester City      15     5      4     6  23  27   
11        12              Aston Villa      16     6      1     9  21  25   
12        13                  Everton      15     5      3     7  19  25   
13        14           Crystal Palace      15     3      7     5  19  21   
14        15             Leeds United      16     3      7     6  17  25   
15        16              Southampton      16     3      7     6  14  24   
16        17                  Watford      16     4      1    11  21  31   
17        18                  Burnley      14     1      7     6  14  21   
18        19         Newcastle United      15     1      7     7  17  30   
19        20             Norwich City      16     2      4    10   8  32   

    Points  
0       38  
1       37  
2       36  
3       27  
4       27  
5       26  
6       25  
7       21  
8       20  
9       20  
10      19  
11      19  
12      18  
13      16  
14      16  
15      16  
16      13  
17      10  
18      10  
19      10

In [ ]:
# load the forecasts we produced in the last session

forecasts21_22 = pd.read_excel("forecasts21_22.xlsx")
forecasts21_22

Unnamed: 0       date                Home team                Away team  \
0             0 2021-08-13                Brentford                  Arsenal   
1             1 2021-08-14        Manchester United             Leeds United   
2             2 2021-08-14           Leicester City  Wolverhampton Wanderers   
3             3 2021-08-14                  Everton              Southampton   
4             4 2021-08-14                  Chelsea           Crystal Palace   
5             5 2021-08-14                  Watford              Aston Villa   
6             6 2021-08-14                  Burnley   Brighton & Hove Albion   
7             7 2021-08-14             Norwich City                Liverpool   
8             8 2021-08-15         Newcastle United          West Ham United   
9             9 2021-08-15        Tottenham Hotspur          Manchester City   
10           10 2021-08-21                Liverpool                  Burnley   
11           11 2021-08-21             Leeds United                  Everton   
12           12 2021-08-21          Manchester City             Norwich City   
13           13 2021-08-21           Crystal Palace                Brentford   
14           14 2021-08-21              Aston Villa         Newcastle United   
15           15 2021-08-21   Brighton & Hove Albion                  Watford   
16           16 2021-08-22  Wolverhampton Wanderers        Tottenham Hotspur   
17           17 2021-08-22              Southampton        Manchester United   
18           18 2021-08-22                  Arsenal                  Chelsea   
19           19 2021-08-23          West Ham United           Leicester City   
20           20 2021-08-28          Manchester City                  Arsenal   
21           21 2021-08-28         Newcastle United              Southampton   
22           22 2021-08-28          West Ham United           Crystal Palace   
23           23 2021-08-28             Norwich City           Leicester City   
24           24 2021-08-28              Aston Villa                Brentford   
25           25 2021-08-28   Brighton & Hove Albion                  Everton   
26           26 2021-08-28                Liverpool                  Chelsea   
27           27 2021-08-29                  Burnley             Leeds United   
28           28 2021-08-29        Tottenham Hotspur                  Watford   
29           29 2021-08-29  Wolverhampton Wanderers        Manchester United   
30           30 2021-09-11           Crystal Palace        Tottenham Hotspur   
31           31 2021-09-11           Leicester City          Manchester City   
32           32 2021-09-11                Brentford   Brighton & Hove Albion   
33           33 2021-09-11        Manchester United         Newcastle United   
34           34 2021-09-11                  Watford  Wolverhampton Wanderers   
35           35 2021-09-11              Southampton          West Ham United   
36           36 2021-09-11                  Arsenal             Norwich City   
37           37 2021-09-11                  Chelsea              Aston Villa   
38           38 2021-09-12             Leeds United                Liverpool   
39           39 2021-09-13                  Everton                  Burnley   
40           40 2021-09-17         Newcastle United             Leeds United   
41           41 2021-09-18  Wolverhampton Wanderers                Brentford   
42           42 2021-09-18                  Burnley                  Arsenal   
43           43 2021-09-18             Norwich City                  Watford   
44           44 2021-09-18                Liverpool           Crystal Palace   
45           45 2021-09-18          Manchester City              Southampton   
46           46 2021-09-18              Aston Villa                  Everton   
47           47 2021-09-19          West Ham United        Manchester United   
48           48 2021-09-19   Brighton & Hove Albion           Leicester City   
49   

In [ ]:
Unplayed = forecasts21_22[['Home team','Away team','notplayed','logitpred']]
Unplayed

Home team                Away team  notplayed logitpred
0                  Brentford                  Arsenal          0         A
1          Manchester United             Leeds United          0         H
2             Leicester City  Wolverhampton Wanderers          0         H
3                    Everton              Southampton          0         H
4                    Chelsea           Crystal Palace          0         H
5                    Watford              Aston Villa          0         A
6                    Burnley   Brighton & Hove Albion          0         A
7               Norwich City                Liverpool          0         A
8           Newcastle United          West Ham United          0         A
9          Tottenham Hotspur          Manchester City          0         A
10                 Liverpool                  Burnley          0         H
11              Leeds United                  Everton          0         A
12           Manchester City             Norwich City          0         H
13            Crystal Palace                Brentford          0         H
14               Aston Villa         Newcastle United          0         H
15    Brighton & Hove Albion                  Watford          0         H
16   Wolverhampton Wanderers        Tottenham Hotspur          0         A
17               Southampton        Manchester United          0         A
18                   Arsenal                  Chelsea          0         A
19           West Ham United           Leicester City          0         A
20           Manchester City                  Arsenal          0         H
21          Newcastle United              Southampton          0         H
22           West Ham United           Crystal Palace          0         H
23              Norwich City           Leicester City          0         A
24               Aston Villa                Brentford          0         H
25    Brighton & Hove Albion                  Everton          0         A
26                 Liverpool                  Chelsea          0         H
27                   Burnley             Leeds United          0         A
28         Tottenham Hotspur                  Watford          0         H
29   Wolverhampton Wanderers        Manchester United          0         A
30            Crystal Palace        Tottenham Hotspur          0         A
31            Leicester City          Manchester City          0         A
32                 Brentford   Brighton & Hove Albion          0         A
33         Manchester United         Newcastle United          0         H
34                   Watford  Wolverhampton Wanderers          0         A
35               Southampton          West Ham United          0         A
36                   Arsenal             Norwich City          0         H
37                   Chelsea              Aston Villa          0         H
38              Leeds United                Liverpool          0         A
39                   Everton                  Burnley          0         H
40          Newcastle United             Leeds United          0         H
41   Wolverhampton Wanderers                Brentford          0         H
42                   Burnley                  Arsenal          0         A
43              Norwich City                  Watford          0         H
44                 Liverpool           Crystal Palace          0         H
45           Manchester City              Southampton          0         H
46               Aston Villa                  Everton          0         H
47           West Ham United        Manchester United          0         A
48    Brighton & Hove Albion           Leicester City          0         A
49         Tottenham Hotspur                  Chelsea          0         A
50         Manchester United              Aston Villa          0         H
51                   Chelsea          Manchester City          0         H
52                   Watford         Newcast

In [ ]:
Unplayed = Unplayed[Unplayed['notplayed']==1].copy()
Unplayed.describe()

notplayed
count      231.0
mean         1.0
std          0.0
min          1.0
25%          1.0
50%          1.0
75%          1.0
max          1.0

In [ ]:
Unplayed['Hpts'] = np.where(Unplayed['logitpred']=="H", 3, 0)
Unplayed['Apts'] = np.where(Unplayed['logitpred']=="H", 0, 3)
Unplayed

Home team                Away team  notplayed logitpred  \
126                  Burnley        Tottenham Hotspur          1         A   
150                Brentford                  Watford          1         H   
151          Manchester City  Wolverhampton Wanderers          1         H   
152                  Chelsea             Leeds United          1         H   
153                  Arsenal              Southampton          1         H   
154                Liverpool              Aston Villa          1         H   
155             Norwich City        Manchester United          1         A   
156   Brighton & Hove Albion        Tottenham Hotspur          1         A   
157           Leicester City         Newcastle United          1         H   
158                  Burnley          West Ham United          1         A   
159           Crystal Palace                  Everton          1         A   
160                Brentford        Manchester United          1         A   
161             Norwich City              Aston Villa          1         A   
162          Manchester City             Leeds United          1         H   
163                  Burnley                  Watford          1         H   
164   Brighton & Hove Albion  Wolverhampton Wanderers          1         A   
165           Crystal Palace              Southampton          1         H   
166                  Arsenal          West Ham United          1         H   
167           Leicester City        Tottenham Hotspur          1         A   
168                  Chelsea                  Everton          1         H   
169                Liverpool         Newcastle United          1         H   
170        Manchester United   Brighton & Hove Albion          1         H   
171                  Watford           Crystal Palace          1         A   
172          West Ham United             Norwich City          1         H   
173              Aston Villa                  Burnley          1         H   
174              Southampton                Brentford          1         H   
175             Leeds United                  Arsenal          1         A   
176                  Everton           Leicester City          1         A   
177  Wolverhampton Wanderers                  Chelsea          1         A   
178         Newcastle United          Manchester City          1         A   
179        Tottenham Hotspur                Liverpool          1         H   
180                Liverpool             Leeds United          1         H   
181  Wolverhampton Wanderers                  Watford          1         H   
182                  Burnley                  Everton          1         A   
183          West Ham United              Southampton          1         H   
184          Manchester City           Leicester City          1         H   
185        Tottenham Hotspur           Crystal Palace          1         H   
186             Norwich City                  Arsenal          1         A   
187              Aston Villa                  Chelsea          1         A   
188   Brighton & Hove Albion                Brentford          1         H   
189         Newcastle United        Manchester United          1         A   
190                  Arsenal  Wolverhampton Wanderers          1         H   
191              Southampton        Tottenham Hotspur          1         A   
192           Crystal Palace             Norwich City          1         H   
193                  Watford          West Ham United          1         A   
194             Leeds United              Aston Villa          1         A   
195           Leicester City                Liverpool          1         A   
196                  Chelsea   Brighton & Hove Albion          1         H   
197                Brentford          Manchester City          1         A   
198                  Everton         Newcastle United          1         H   
199        Manchester United             

In [ ]:
Results = Unplayed[['Home team','Hpts']].rename(columns={'Home team': 'club','Hpts':'XPoints'})
Results

club  XPoints
126                  Burnley        0
150                Brentford        3
151          Manchester City        3
152                  Chelsea        3
153                  Arsenal        3
154                Liverpool        3
155             Norwich City        0
156   Brighton & Hove Albion        0
157           Leicester City        3
158                  Burnley        0
159           Crystal Palace        0
160                Brentford        0
161             Norwich City        0
162          Manchester City        3
163                  Burnley        3
164   Brighton & Hove Albion        0
165           Crystal Palace        3
166                  Arsenal        3
167           Leicester City        0
168                  Chelsea        3
169                Liverpool        3
170        Manchester United        3
171                  Watford        0
172          West Ham United        3
173              Aston Villa        3
174              Southampton        3
175             Leeds United        0
176                  Everton        0
177  Wolverhampton Wanderers        0
178         Newcastle United        0
179        Tottenham Hotspur        3
180                Liverpool        3
181  Wolverhampton Wanderers        3
182                  Burnley        0
183          West Ham United        3
184          Manchester City        3
185        Tottenham Hotspur        3
186             Norwich City        0
187              Aston Villa        0
188   Brighton & Hove Albion        3
189         Newcastle United        0
190                  Arsenal        3
191              Southampton        0
192           Crystal Palace        3
193                  Watford        0
194             Leeds United        0
195           Leicester City        0
196                  Chelsea        3
197                Brentford        0
198                  Everton        3
199        Manchester United        3
200                  Arsenal        0
201                  Watford        0
202           Leicester City        3
203           Crystal Palace        0
204                  Everton        3
205                Brentford        0
206              Southampton        3
207             Leeds United        3
208                  Chelsea        3
209        Manchester United        3
210   Brighton & Hove Albion        3
211          Manchester City        3
212         Newcastle United        3
213  Wolverhampton Wanderers        3
214                  Burnley        0
215                Liverpool        3
216             Norwich City        0
217              Aston Villa        0
218          West Ham United        3
219        Tottenham Hotspur        3
220                  Watford        0
221                  Everton        3
222             Leeds United        3
223                Brentford        0
224        Manchester United        3
225                  Arsenal        3
226              Southampton        0
227           Leicester City        3
228           Crystal Palace        0
229                  Chelsea        3
230             Norwich City        0
231              Aston Villa        3
232   Brighton & Hove Albion        0
233  Wolverhampton Wanderers        0
234                  Burnley        0
235          West Ham United        3
236         Newcastle United        0
237        Tottenham Hotspur        3
238                Liverpool        3
239          Manchester City        3
240                  Watford        0
241         Newcastle United        0
242                  Chelsea        3
243                  Everton        3
244             Norwich City        0
245                  Burnley        0
246        Manchester United        3
247        Tottenham Hotspur        3
248                Brentford        3
249           Leicester City        3
250              Southampton        0
251           Crystal Palace        0
252  Wolverhampton Wanderers        0
253                  Arsenal      

In [ ]:
AResults = Unplayed[['Away team','Apts']].rename(columns={'Away team': 'club','Apts':'XPoints'})
AResults

club  XPoints
126        Tottenham Hotspur        3
150                  Watford        0
151  Wolverhampton Wanderers        0
152             Leeds United        0
153              Southampton        0
154              Aston Villa        0
155        Manchester United        3
156        Tottenham Hotspur        3
157         Newcastle United        0
158          West Ham United        3
159                  Everton        3
160        Manchester United        3
161              Aston Villa        3
162             Leeds United        0
163                  Watford        0
164  Wolverhampton Wanderers        3
165              Southampton        0
166          West Ham United        0
167        Tottenham Hotspur        3
168                  Everton        0
169         Newcastle United        0
170   Brighton & Hove Albion        0
171           Crystal Palace        3
172             Norwich City        0
173                  Burnley        0
174                Brentford        0
175                  Arsenal        3
176           Leicester City        3
177                  Chelsea        3
178          Manchester City        3
179                Liverpool        0
180             Leeds United        0
181                  Watford        0
182                  Everton        3
183              Southampton        0
184           Leicester City        0
185           Crystal Palace        0
186                  Arsenal        3
187                  Chelsea        3
188                Brentford        0
189        Manchester United        3
190  Wolverhampton Wanderers        0
191        Tottenham Hotspur        3
192             Norwich City        0
193          West Ham United        3
194              Aston Villa        3
195                Liverpool        3
196   Brighton & Hove Albion        0
197          Manchester City        3
198         Newcastle United        0
199                  Burnley        0
200          Manchester City        3
201        Tottenham Hotspur        3
202             Norwich City        0
203          West Ham United        3
204   Brighton & Hove Albion        0
205              Aston Villa        3
206         Newcastle United        0
207                  Burnley        0
208                Liverpool        0
209  Wolverhampton Wanderers        0
210           Crystal Palace        0
211                  Chelsea        0
212                  Watford        0
213              Southampton        0
214           Leicester City        3
215                Brentford        0
216                  Everton        3
217        Manchester United        3
218             Leeds United        0
219                  Arsenal        0
220             Norwich City        3
221              Aston Villa        0
222         Newcastle United        0
223  Wolverhampton Wanderers        3
224          West Ham United        0
225                  Burnley        0
226          Manchester City        3
227   Brighton & Hove Albion        0
228                Liverpool        3
229        Tottenham Hotspur        0
230           Crystal Palace        3
231             Leeds United        0
232                  Chelsea        3
233                  Arsenal        3
234        Manchester United        3
235                  Watford        0
236                  Everton        3
237              Southampton        0
238           Leicester City        0
239                Brentford        0
240   Brighton & Hove Albion        3
241              Aston Villa        3
242                  Arsenal        0
243             Leeds United        0
244          Manchester City        3
245                Liverpool        3
246              Southampton        0
247  Wolverhampton Wanderers        0
248           Crystal Palace        0
249          West Ham United        0
250                  Everton        3
251                  Chelsea        3
252           Leicester City        3
253                Brentford      

In [ ]:
Results = pd.concat([Results, AResults])
Results

club  XPoints
126           Burnley        0
150         Brentford        3
151   Manchester City        3
152           Chelsea        3
153           Arsenal        3
..                ...      ...
375           Watford        0
376       Aston Villa        0
377  Newcastle United        3
378       Southampton        0
379           Everton        0

[462 rows x 2 columns]

In [ ]:
Results.describe()

XPoints
count  462.000000
mean     1.500000
std      1.501626
min      0.000000
25%      0.000000
50%      1.500000
75%      3.000000
max      3.000000

In [ ]:
PtsX = Results.groupby('club')['XPoints'].sum().reset_index()
PtsX

club  XPoints
0                   Arsenal       54
1               Aston Villa       36
2                 Brentford       15
3    Brighton & Hove Albion       18
4                   Burnley        3
5                   Chelsea       63
6            Crystal Palace       21
7                   Everton       39
8              Leeds United       21
9            Leicester City       45
10                Liverpool       60
11          Manchester City       69
12        Manchester United       63
13         Newcastle United       15
14             Norwich City        9
15              Southampton       21
16        Tottenham Hotspur       60
17                  Watford        3
18          West Ham United       45
19  Wolverhampton Wanderers       33

In [ ]:
Table = pd.merge(Table, PtsX, on= 'club', how = 'left')
Table

Position                     club  Played  Won   Drawn  Lost   F   A  \
0          1          Manchester City      16    12      2     2  33   9   
1          2                Liverpool      16    11      4     1  45  12   
2          3                  Chelsea      16    11      3     2  38  11   
3          4          West Ham United      15     8      3     4  28  19   
4          5        Manchester United      16     8      3     5  26  24   
5          6                  Arsenal      16     8      2     6  21  22   
6          7        Tottenham Hotspur      14     8      1     5  16  17   
7          8  Wolverhampton Wanderers      16     6      3     7  12  14   
8          9                Brentford      16     5      5     6  21  22   
9         10   Brighton & Hove Albion      15     4      8     3  14  16   
10        11           Leicester City      15     5      4     6  23  27   
11        12              Aston Villa      16     6      1     9  21  25   
12        13                  Everton      15     5      3     7  19  25   
13        14           Crystal Palace      15     3      7     5  19  21   
14        15             Leeds United      16     3      7     6  17  25   
15        16              Southampton      16     3      7     6  14  24   
16        17                  Watford      16     4      1    11  21  31   
17        18                  Burnley      14     1      7     6  14  21   
18        19         Newcastle United      15     1      7     7  17  30   
19        20             Norwich City      16     2      4    10   8  32   

    Points  XPoints  
0       38       69  
1       37       60  
2       36       63  
3       27       45  
4       27       63  
5       26       54  
6       25       60  
7       21       33  
8       20       15  
9       20       18  
10      19       45  
11      19       36  
12      18       39  
13      16       21  
14      16       21  
15      16       21  
16      13        3  
17      10        3  
18      10       15  
19      10        9

In [ ]:
Table['finalpoints']=Table['Points']+ Table['XPoints']
Table

Position                     club  Played  Won   Drawn  Lost   F   A  \
0          1          Manchester City      16    12      2     2  33   9   
1          2                Liverpool      16    11      4     1  45  12   
2          3                  Chelsea      16    11      3     2  38  11   
3          4          West Ham United      15     8      3     4  28  19   
4          5        Manchester United      16     8      3     5  26  24   
5          6                  Arsenal      16     8      2     6  21  22   
6          7        Tottenham Hotspur      14     8      1     5  16  17   
7          8  Wolverhampton Wanderers      16     6      3     7  12  14   
8          9                Brentford      16     5      5     6  21  22   
9         10   Brighton & Hove Albion      15     4      8     3  14  16   
10        11           Leicester City      15     5      4     6  23  27   
11        12              Aston Villa      16     6      1     9  21  25   
12        13                  Everton      15     5      3     7  19  25   
13        14           Crystal Palace      15     3      7     5  19  21   
14        15             Leeds United      16     3      7     6  17  25   
15        16              Southampton      16     3      7     6  14  24   
16        17                  Watford      16     4      1    11  21  31   
17        18                  Burnley      14     1      7     6  14  21   
18        19         Newcastle United      15     1      7     7  17  30   
19        20             Norwich City      16     2      4    10   8  32   

    Points  XPoints  finalpoints  
0       38       69          107  
1       37       60           97  
2       36       63           99  
3       27       45           72  
4       27       63           90  
5       26       54           80  
6       25       60           85  
7       21       33           54  
8       20       15           35  
9       20       18           38  
10      19       45           64  
11      19       36           55  
12      18       39           57  
13      16       21           37  
14      16       21           37  
15      16       21           37  
16      13        3           16  
17      10        3           13  
18      10       15           25  
19      10        9           19

In [ ]:
Table.sort_values("finalpoints", inplace = True, ascending = False)
Table['rank'] = Table['finalpoints'].rank(ascending= False)
Table

Position                     club  Played  Won   Drawn  Lost   F   A  \
0          1          Manchester City      16    12      2     2  33   9   
2          3                  Chelsea      16    11      3     2  38  11   
1          2                Liverpool      16    11      4     1  45  12   
4          5        Manchester United      16     8      3     5  26  24   
6          7        Tottenham Hotspur      14     8      1     5  16  17   
5          6                  Arsenal      16     8      2     6  21  22   
3          4          West Ham United      15     8      3     4  28  19   
10        11           Leicester City      15     5      4     6  23  27   
12        13                  Everton      15     5      3     7  19  25   
11        12              Aston Villa      16     6      1     9  21  25   
7          8  Wolverhampton Wanderers      16     6      3     7  12  14   
9         10   Brighton & Hove Albion      15     4      8     3  14  16   
13        14           Crystal Palace      15     3      7     5  19  21   
14        15             Leeds United      16     3      7     6  17  25   
15        16              Southampton      16     3      7     6  14  24   
8          9                Brentford      16     5      5     6  21  22   
18        19         Newcastle United      15     1      7     7  17  30   
19        20             Norwich City      16     2      4    10   8  32   
16        17                  Watford      16     4      1    11  21  31   
17        18                  Burnley      14     1      7     6  14  21   

    Points  XPoints  finalpoints  rank  
0       38       69          107   1.0  
2       36       63           99   2.0  
1       37       60           97   3.0  
4       27       63           90   4.0  
6       25       60           85   5.0  
5       26       54           80   6.0  
3       27       45           72   7.0  
10      19       45           64   8.0  
12      18       39           57   9.0  
11      19       36           55  10.0  
7       21       33           54  11.0  
9       20       18           38  12.0  
13      16       21           37  14.0  
14      16       21           37  14.0  
15      16       21           37  14.0  
8       20       15           35  16.0  
18      10       15           25  17.0  
19      10        9           19  18.0  
16      13        3           16  19.0  
17      10        3           13  20.0